In [2]:
%load_ext autoreload
%autoreload 2

import gymnasium as gym
from gymnasium import spaces
import numpy as np
import mujoco
import os

import gymnasium as gym
import numpy as np
from gymnasium import spaces

from gymnasium.utils.env_checker import check_env

# Cмотрим как отработал
from robot_env import RobotGo1Env

In [3]:
xml_path = 'robot_models/unitree_go1/scene.xml'

model = mujoco.MjModel.from_xml_path(xml_path)
data = mujoco.MjData(model)

# При mj_resetData автоматически загружается keyframe "home"
mujoco.mj_resetData(model, data)

print("qpos:", data.qpos)
print("qvel:", data.qvel)

qpos: [0.    0.    0.445 1.    0.    0.    0.    0.    0.    0.    0.    0.
 0.    0.    0.    0.    0.    0.    0.   ]
qvel: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


In [48]:
data.sensor("orientation").data

KeyError: "Invalid name 'orientation'. Valid names: []"

In [ ]:
data.body("trunk").

array([0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [ ]:
data.sensordata

array([], dtype=float64)

In [ ]:
# Информация о всех текущих контактах
for i in range(data.ncon):
    contact = data.contact[i]
    geom1 = contact.geom1
    geom2 = contact.geom2
    force = contact.force
    print(f"Контакт между {geom1} и {geom2}, сила: {force}")

In [ ]:
data.ncon

0

In [ ]:
data.qfrc_actuator

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0.])

In [ ]:
len(data.qpos)

19

In [ ]:
class RobotLearning(gym.Env):
    # metadata is a required attribute
    # render_modes in our environment is either None or 'human'.
    # render_fps is not used in our env, but we are require to declare a non-zero value.
    metadata = {"render_modes": ["human"], 'render_fps': 4}

    def __init__(self, xml_path):
        super().__init__()

        self.model = mujoco.MjModel.from_xml_path(xml_path)
        self.data = mujoco.MjData(self.model)
        
        self.reward = None
        # Параметры времени шаг времени в секундах
        self.dt = self.model.opt.timestep
                        
        # Установим максимальное время с начсала эпизода в секундах
        # Те эпизод не может длится более 100сек, собака может идти 100сек, далее trancked
        self.max_episode_time = 10      # максимальное время эпизода в секундах
        self.max_episode_steps = int(self.max_episode_time / self.dt)  # в шагах
        
        # Трекинг времени
        self.current_episode_time = 0
        self.current_episode_steps = 0


        self.qpos = None
        self.qvel = None


        free_joint = np.array([[-np.inf, np.inf], # Для X
                                [-np.inf, np.inf], # Для Y
                                [0, 10], # Для Z (условно поставили, что робот не может уйти под пол и взлетететь на 10м вверх)
                                [-1, 1], # w - действительная часть кватерниона Определяет величину поворота w = cos(θ/2),  где θ - угол поворота
                                [-1, 1], # x - ось вращения по x
                                [-1, 1], # y - ось вращения по y
                                [-1, 1], # z - ось вращения по z
                ])

        # В массиве есть ограничения на qpos (углы поворота) и я беру нижнюю и верхнюю границы
        # Функция выдает model.jnt_range выдает ограничения на углы в модели, на углу joint 
        # Мне всегдла выдаются, нижнее и верхнее ограничение, поэтому беру первое значение и второе.

        # ограничения на FR, FL, RR, RL ноги 
        # model.jnt_range[1:]  (нулевой выкидываем, тк он равен 0 - это free_joint, для него мы отдельно выше )
        hinge_joints = self.model.jnt_range[1:] 
        

        qpos_low = np.concatenate([free_joint, hinge_joints])[:,0]
        qpos_high = np.concatenate([free_joint, hinge_joints])[:,1]

        # Define what the agent can observe
        # Dict space gives us structured, human-readable observations
        self.observation_space = gym.spaces.Dict(
            {   

                # array([[ 0.   ,  0.   ],
                #    [-0.863,  0.863],
                #    [-0.686,  4.501],
                #    [-2.818, -0.888],
                #    [-0.863,  0.863],
                # model.actuator_forcerange ограничения поданные на акуатор
                 "qpos": gym.spaces.Box(low = qpos_low, high = qpos_high,  shape=(self.model.nq,), dtype=np.float32),   #  углы с ограничениями
                 "qvel": gym.spaces.Box(low = -np.inf ,high = np.inf, shape=(self.model.nu,), dtype=np.float32),  # [x, y] coordinates
            }
        )


            #    "qpos": gym.spaces.Box(low = model.jnt_range[:,0], high = model.jnt_range[:,1],  shape=(model.jnt_range.shape[0],), dtype=np.float32),   #  углы с ограничениями
            #      "qvel": gym.spaces.Box(low = model.actuator_forcerange[:,0] ,high = model.actuator_forcerange[:,1], shape=(model.actuator_forcerange.shape[0],), dtype=np.float32),  # [x, y] coordinates
  

        # Здесь ставим ограничения актуаторов: нижняя и верхняя границы 
        self.action_space = gym.spaces.Box(low = self.model.actuator_ctrlrange[:,0] ,high = self.model.actuator_ctrlrange[:,1], shape=(self.model.nu,), dtype=np.float32)

    def _get_obs(self):
        """Convert internal state to observation format.

        Returns:
            dict: Observation with agent and target positions
        """

        qpos = np.float32(self.data.qpos.copy())
        
        # Берем только скорости ног, первые 6 выкидываем, тк это скорость тела frejoint
        qvel = np.float32(self.data.qvel[6:].copy())
        
        observation_space = {
                "qpos": qpos,  # координаты 
                "qvel": qvel,  # скорости
            }
        
        
        return observation_space
    
    def _get_info(self):
        """Compute auxiliary information for debugging.

        Returns:
            dict: Info with distance between agent and target
        """
        qpose = self.data.qpos.copy()
        qvel = self.data.qvel.copy()
        is_terminate= None
        is_trancate = None
        
        info = {
                "qpos": qpose, # координаты 
                "qvel": qvel,  # скорости
                'is_terminate':is_terminate,
                'is_trancate': is_trancate,

            }
        
        return info
    
    def reset(self, seed=None, options=None):

         # IMPORTANT: Must call this first to seed the random number generator
        super().reset(seed=seed)
        
        mujoco.mj_resetData(self.model, self.data)

        self.current_episode_time = 0
        self.current_episode_steps = 0

 
        
        #  Рандомная инициализация углов ног.
        # !!!! Улучшить эту часть с помощью рандома
        # Вовзращает в состоанияе keyframe, те
        # <keyframe>
        #     <key name="home" qpos="0 0 0.27 1 0 0 0 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8"
        #     ctrl="0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8"/>
        # </keyframe>
        key_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_KEY, 'home')
        if key_id >= 0:
            # Устанавливаем состояние из ключевого кадра
            mujoco.mj_resetDataKeyframe(self.model, self.data, key_id)
        else:
            # Если ключевого кадра нет, используем обычный сброс
            mujoco.mj_resetData(self.model, self.data)

        # Если устаналивать в key позу, то можно это не писать, тк это автоматически сделаемся в
        # mujoco.mj_resetDataKeyframe(self.model, self.data, key_id)
        self.qpos = self.data.qpos.copy()
        self.qvel = self.data.qvel.copy()


        mujoco.mj_forward(self.model, self.data)

        observation = self._get_obs()
        info = self._get_info()
        
        return observation, info
    

    def _is_terminated(self):
        # trunk_body_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_BODY, "trunk")
        # trunk_position = data.xpos[trunk_body_id]  # [x, y, z] в метрах

        hight_on_floor = self.data.qpos[2] # Берем координату Z

        if hight_on_floor < 0.05:
            return True
        return False
        

    def _is_truncated(self):
        if self.current_episode_time >= self.max_episode_steps or \
            self.current_episode_steps >= self.max_episode_steps: 
            return True
        return False
    
    def _compute_reward(self, prev_qpos):
        prev_x = prev_qpos[0]
        current_x = self.data.qpos[0]

        self.reward = np.linalg.norm(current_x - prev_x)

        return self.reward

        
    def step(self, action):
        # Предыдущие значения qpos сохраняем для расчета награды
        prev_qpos = self.data.qpos.copy()

        self.data.ctrl[:] = action
        mujoco.mj_step(self.model, self.data)

        self.current_episode_time += self.dt
        self.current_episode_steps +=1

        observation = self._get_obs()
        info = self._get_info()

        reward = self._compute_reward(prev_qpos)
        terminated = self._is_terminated()
        truncated = self._is_truncated()


        # Добавляпм в info
        info.update({
            'reward' : reward,
            'terminated' : terminated,
            'truncated' : truncated
        })


        return observation, reward, terminated, truncated, info

    def render(self):
        """- Renders the environments to help visualise what the agent see, examples modes are “human”, “rgb_array”, “ansi” for text."""
        pass

    def close(self):
        pass

In [ ]:
xml_path = 'robot_models/unitree_go1/scene.xml'

robot_env = RobotLearning(xml_path)

check_env(robot_env)

/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:305: UserWarning: WARN: Box high's precision lowered by casting to float32, current high.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/utils/env_checker.py:333: UserWarning: WARN: For Box action spaces, we recommend using a symmetric and normalized space (range=[-1, 1] or [0, 1]). See https://stable-baselines3.readthedocs.io/en/master/guide/rl_tips.html for more information.
  logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/utils/env_checker.py:311: UserWarning: WARN: A Box observation space minimum value is -infinity. This is probably too low.
  logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymn

In [ ]:
qpos = [
    # Free joint (7 элементов)
    0, 0, 0.27,       # позиция: x=0, y=0, z=0.27м (над полом)
    1, 0, 0, 0,       # ориентация: единичный кватернион (без поворота)
    
    # Суставы (12 элементов)
    # FR: 0, 0.9, -1.8
    # FL: 0, 0.9, -1.8  
    # RR: 0, 0.9, -1.8
    # RL: 0, 0.9, -1.8
    0, 0.9, -1.8,     # FR_abduction, FR_hip, FR_knee
    0, 0.9, -1.8,     # FL_abduction, FL_hip, FL_knee  
    0, 0.9, -1.8,     # RR_abduction, RR_hip, RR_knee
    0, 0.9, -1.8      # RL_abduction, RL_hip, RL_knee
]

In [ ]:
data.qpos

array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   ])

In [ ]:
data.qfrc_actuator[7:19]

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [ ]:
joint_torques = data.qfrc_actuator[7:19]
joint_velocities = data.qvel[6:18]
    
# Положительная мощность = потребление энергии
# Отрицательная мощность = регенерация (возврат энергии)
joint_powers = joint_torques * joint_velocities

joint_powers

ValueError: operands could not be broadcast together with shapes (11,) (12,) 

In [ ]:

    def _get_foot_contacts(self):
        """Определение контактов ног с землей"""
        foot_contacts = np.zeros(4)
        foot_sites = ["FL_foot", "FR_foot", "RL_foot", "RR_foot"]
        
        for i, site_name in enumerate(foot_sites):
            site_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_SITE, site_name)
            if site_id != -1:
                # Определяем контакт по высоте и силе
                foot_height = self.data.site_xpos[site_id][2]
                foot_contacts[i] = 1.0 if foot_height < 0.03 else 0.0
                
        return foot_contacts

In [ ]:
data.qpos[3:7]

array([1., 0., 0., 0.])

In [ ]:
data.qpos

array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   ])

In [ ]:
len(data.qvel)

18

In [ ]:
data.qvel[0:3]

array([0., 0., 0.])

In [ ]:
# 'FR_qpos' : self.data.qpos[0:3]  # hip, thigh, calf
# 'FL_qpos'
# 'RR_qpos'
# 'RL_qpos'



In [6]:
data.qvel

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0.])

In [7]:
data.qvel[15:18]

array([0., 0., 0.])

In [11]:
len(data.qfrc_actuator)

18

In [12]:
len(data.qvel)

18

In [ ]:
    joint_power = np.abs(self.data.qfrc_actuator[7:19] * self.data.qvel[6:18])
    total_power = np.sum(joint_power)

In [14]:
data.qfrc_actuator[7:19]

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [ ]:
from scipy.spatial.transform import Rotation

#20 см в секунду
self.target_linear_velocity = 20 

# если qw - кватернион ближе |qw| к 1, тем ближе ориентация к "прямой" 
# если qw близко к 0 - робот сильно наклонен или перевернут)
self.vertical_orientation = 1 
self.target_roll, pitch, yaw


roll, pitch, yaw = np.float32(Rotation.from_quat(self.data.qpos[3:7], scalar_first=True).as_euler('xyz', degrees=True))
joint_power = 

{


# qpos[0:3] для free joint - это абсолютные мировые координаты, 
# которые недоступны на реальном роботе. 
# Поэтому в обучении следует использовать только относительные измерения 
# Точнее именно в observation

#roll, pitch, yaw

#'free_joint_orientation' : data.qpos[3:7], # qw, qx, qy, qz1.  example: [1 , 0.   , 0.   , 0 ] 
'free_joint_linear_velocity' : self.data.qvel[0:3],  # Линейная скорость
'free_joint_angular_velocity' : self.data.qvel[3:6], # УГловая скорость
'free_joint_vertical_orientation'  : self.data.qpos[3], # вертикальная ориентация qw - кватернион скалярная часть
'free_joint_euler_orientation': np.float32(Rotation.from_quat(self.data.qpos[3:7], scalar_first=True).as_euler('xyz', degrees=True)),


'FR_qpos' : data.qpos[7:10],  # hip, thigh, calf
'FL_qpos' : data.qpos[10:13],
'RR_qpos' : data.qpos[13:16],
'RL_qpos' : data.qpos[16:19],

# qvel = [
#     # СВОБОДНОЕ СОЕДИНЕНИЕ (6):
#     0: vx, 1: vy, 2: vz,         # линейная скорость (3)
#     3: wx, 4: wy, 5: wz,         # угловая скорость (3)
#     # СУСТАВЫ НОГ (12):
#     6: FR_hip, 7: FR_thigh, 8: FR_calf,      # 6-8
#     9: FL_hip, 10: FL_thigh, 11: FL_calf,    # 9-11
#     12: RR_hip, 13: RR_thigh, 14: RR_calf,   # 12-14
#     15: RL_hip, 16: RL_thigh, 17: RL_calf    # 15-17
# ]
'FR_qvel' : data.qvel[6:9],
'FL_qvel' : data.qvel[9:12],
'RR_qvel' : data.qvel[12:15],
'RL_qvel' : data.qvel[15:18]

## мощности:
'FR_power'
'FL_power'
'RR_power'
'RL_power'




}

{'free_joint_orientation': array([1., 0., 0., 0.]),
 'free_joint_linear': array([0., 0., 0.])}

In [14]:
!pipreqs

Unexpected exception formatting exception. Falling back to standard exception

[autoreload of IPython.core.magics.packaging failed: Traceback (most recent call last):
  File "/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/IPython/extensions/autoreload.py", line 325, in check
    for key in list(old.__dict__.keys()):
                        ^^^^^^^^^^^^^^^^^^
  File "/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/IPython/extensions/autoreload.py", line 621, in superreload
    if args.print is False and args.log is False:
        ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/IPython/extensions/autoreload.py", line 447, in update_generic
    old_objects = {}
        ^^^^^^^^^^^^
  File "/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/IPython/extensions/autoreload.py", line 399, in update_class
    def __init__(self, obj):
           ^^^^^^^^^^^^^^^^^^
  File "/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/IPython/extensions/autoreload.py", line 447, in update_generic
    

In [62]:
data.qvel

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0.])

In [ ]:
observation_space = 
{
    # Туловище
    #free_joint x, y, z  
    free_joint_quaternion qw, qx, qy, qz,
    #"высота туловища над землей":
    'линейная скорость'
    'угловая скорость'

    ### Ноги 
    
    ## углы
    'FR_qpos'
    'FL_qpos'
    'RR_qpos'
    'RL_qpos'

    ## cкорости
    'FR_qvel'
    'FL_qvel'
    'RR_qvel'
    'RL_qvel'

    ## мощности:
    'FR_power'
    'FL_power'
    'RR_power'
    'RL_power'

    ## cила контакта
    'FR_power'
    'FL_power'
    'RR_power'
    'RL_power'

    "на_сколько_высоко_над_землей FR knee": 
    "на_сколько_высоко_над_землей FL knee"
    "на_сколько_высоко_над_землей RR knee"
    "на_сколько_высоко_над_землей RL knee"

    "есть ли касание с землей FR" [0,1]
    "есть ли касание с землей FL" [0,1]
    "есть ли касание с землей RR" [0,1]
    "есть ли касание с землей RL" [0,1]

    # Дополнительные
    "кол-во касаний в данный момент"
    Таргет:
        - иди со скоростью 20см в секунду
    
    Ограничения:
        - суставы в ноль плечевые
        - координата по Y = 0 
        - идеальная коорданаты по Z около 2-3м
        - суставные углы в определенном диапозоне: отклонение от него 

    
}


action_space = 
{
    # Передняя правая нога (FR)
    FR_hip_control,     # 0 - отведение/приведение
    FR_thigh_control,   # 1 - бедро  
    FR_calf_control,    # 2 - колено
    
    # Передняя левая нога (FL)
    FL_hip_control,     # 3
    FL_thigh_control,   # 4
    FL_calf_control,    # 5
    
    # Задняя правая нога (RR)  
    RR_hip_control,     # 6
    RR_thigh_control,   # 7
    RR_calf_control,    # 8
    
    # Задняя левая нога (RL)
    RL_hip_control,     # 9
    RL_thigh_control,   # 10
    RL_calf_control,    # 11
}

    ----
    "foot_contacts": gym.spaces.MultiBinary(4),  # 4 стопы
    "contact_forces": gym.spaces.Box(0, np.inf, (4,)),  # силы контакта

In [ ]:
        self.qpos = None
        self.qvel = None


        free_joint = np.array([[-np.inf, np.inf], # Для X
                                [-np.inf, np.inf], # Для Y
                                [0, 10], # Для Z (условно поставили, что робот не может уйти под пол и взлетететь на 10м вверх)
                                [-1, 1], # w - действительная часть кватерниона Определяет величину поворота w = cos(θ/2),  где θ - угол поворота
                                [-1, 1], # x - ось вращения по x
                                [-1, 1], # y - ось вращения по y
                                [-1, 1], # z - ось вращения по z
                ])

        # В массиве есть ограничения на qpos (углы поворота) и я беру нижнюю и верхнюю границы
        # Функция выдает model.jnt_range выдает ограничения на углы в модели, на углу joint 
        # Мне всегдла выдаются, нижнее и верхнее ограничение, поэтому беру первое значение и второе.

        # ограничения на FR, FL, RR, RL ноги 
        # model.jnt_range[1:]  (нулевой выкидываем, тк он равен 0 - это free_joint, для него мы отдельно выше )
        hinge_joints = self.model.jnt_range[1:] 
        

        qpos_low = np.concatenate([free_joint, hinge_joints])[:,0]
        qpos_high = np.concatenate([free_joint, hinge_joints])[:,1]

        # Define what the agent can observe
        # Dict space gives us structured, human-readable observations
        self.observation_space = gym.spaces.Dict(
            {   

                # array([[ 0.   ,  0.   ],
                #    [-0.863,  0.863],
                #    [-0.686,  4.501],
                #    [-2.818, -0.888],
                #    [-0.863,  0.863],
                # model.actuator_forcerange ограничения поданные на акуатор
                 "qpos": gym.spaces.Box(low = qpos_low, high = qpos_high,  shape=(self.model.nq,), dtype=np.float32),   #  углы с ограничениями
                 "qvel": gym.spaces.Box(low = -np.inf ,high = np.inf, shape=(self.model.nu,), dtype=np.float32),  # [x, y] coordinates
            }
        )


            #    "qpos": gym.spaces.Box(low = model.jnt_range[:,0], high = model.jnt_range[:,1],  shape=(model.jnt_range.shape[0],), dtype=np.float32),   #  углы с ограничениями
            #      "qvel": gym.spaces.Box(low = model.actuator_forcerange[:,0] ,high = model.actuator_forcerange[:,1], shape=(model.actuator_forcerange.shape[0],), dtype=np.float32),  # [x, y] coordinates
  

        # Здесь ставим ограничения актуаторов: нижняя и верхняя границы 
        self.action_space = gym.spaces.Box(low = self.model.actuator_ctrlrange[:,0] ,high = self.model.actuator_ctrlrange[:,1], shape=(self.model.nu,), dtype=np.float32)


In [ ]:
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.callbacks import CheckpointCallback, EvalCallback


# checkpoint_callback = CheckpointCallback(
#     save_freq=1_000_000,
#     save_path="train_models/current_model/",
#     name_prefix="go1_ppo"
# )

eval_callback = EvalCallback(
    robot_env,
    best_model_save_path="train_models/best/",
    log_path="logs/",
    eval_freq=1000000,
    n_eval_episodes=5, 
    deterministic=True,
    render=False
)


In [ ]:
from stable_baselines3.common.callbacks import BaseCallback

class SmartCheckpointCallback(BaseCallback):
    def __init__(self, save_freq: int, save_path: str, name_prefix: str, initial_step: int = 0, verbose=0):
        super(SmartCheckpointCallback, self).__init__(verbose)
        self.save_freq = save_freq
        self.save_path = save_path
        self.name_prefix = name_prefix
        self.initial_step = initial_step
        self.last_save = initial_step
        
        os.makedirs(save_path, exist_ok=True)

    def _on_step(self) -> bool:
        total_steps = self.initial_step + self.num_timesteps
        
        if total_steps - self.last_save >= self.save_freq:
            model_path = os.path.join(self.save_path, f"{self.name_prefix}_{total_steps}_steps")
            self.model.save(model_path)
            print(f"Сохранена модель: {model_path}")
            self.last_save = total_steps
            
        return True
    

# Использование
checkpoint_callback = SmartCheckpointCallback(
    initial_step=0,  # Начинаем с 2 млн шагов
    save_freq=1000000,       # Сохранять каждые 100к шагов
    save_path="train_models/current_model/",
    name_prefix="go1_ppo",
    verbose=1
)


In [ ]:
from stable_baselines3.common.callbacks import BaseCallback
import numpy as np

class TensorboardCallback(BaseCallback):
    def __init__(self, verbose=0):
        super(TensorboardCallback, self).__init__(verbose)
        self.episode_rewards = []
        self.episode_lengths = []
        self.current_episode_reward = 0
        self.current_episode_length = 0
        
    def _on_step(self) -> bool:
        # Получаем информацию из среды
        if len(self.locals['infos']) > 0:
            info = self.locals['infos'][0]
            
            # Накапливаем награду за эпизод
            self.current_episode_reward += self.locals['rewards'][0]
            self.current_episode_length += 1
            
            # Если эпизод завершен
            if info.get('terminated', False) or info.get('truncated', False):
                self.episode_rewards.append(self.current_episode_reward)
                self.episode_lengths.append(self.current_episode_length)
                
                # Логируем в TensorBoard
                if len(self.episode_rewards) > 0:
                    self.logger.record('train/episode_reward', self.current_episode_reward)
                    self.logger.record('train/episode_length', self.current_episode_length)
                    self.logger.record('train/mean_episode_reward', np.mean(self.episode_rewards))
                    self.logger.record('train/mean_episode_length', np.mean(self.episode_lengths))
                
                # Сбрасываем счетчики
                self.current_episode_reward = 0
                self.current_episode_length = 0
                
        return True

# Добавьте этот callback в список
tensorboard_callback = TensorboardCallback()

In [ ]:
import gymnasium as gym

from stable_baselines3 import PPO
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.vec_env import DummyVecEnv, SubprocVecEnv

# Parallel environments
#vec_env = make_vec_env(robot_env)
#vec_env = make_vec_env("CartPole-v1", n_envs=4)

# Создание векторной среды
env = make_vec_env(
    lambda: RobotLearning(xml_path='robot_models/unitree_go1/scene.xml'),
    n_envs=4,           # Количество параллельных сред
    vec_env_cls=DummyVecEnv  # Тип векторной среды
)


model = PPO("MultiInputPolicy", 
            #robot_env, 
            env,
            tensorboard_log="./ppo_tensorboard_logs/",
            n_steps  = 4096,
            batch_size = 128,
            n_epochs=10,
            verbose=1)

# model = PPO.load("train_models/current_model/go1_ppo_4000000_steps", env=robot_env)  

model.learn(total_timesteps=3_000_000, callback=[checkpoint_callback, eval_callback,  tensorboard_callback])
model.save("train_models/go1")





Using cpu device
Logging to ./ppo_tensorboard_logs/PPO_12
------------------------------
| time/              |       |
|    fps             | 4185  |
|    iterations      | 1     |
|    time_elapsed    | 3     |
|    total_timesteps | 16384 |
------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 5e+03      |
|    ep_rew_mean          | 1.06e+03   |
| time/                   |            |
|    fps                  | 3048       |
|    iterations           | 2          |
|    time_elapsed         | 10         |
|    total_timesteps      | 32768      |
| train/                  |            |
|    approx_kl            | 0.01034102 |
|    clip_fraction        | 0.105      |
|    clip_range           | 0.2        |
|    entropy_loss         | -17        |
|    episode_length       | 8664       |
|    episode_reward       | 4.49e+03   |
|    explained_variance   | -0.0271    |
|    learning_rate        | 

/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=985344, episode_reward=2098.87 +/- 0.00
Episode length: 5000.00 +/- 0.00
----------------------------------------
| eval/                   |            |
|    mean_ep_length       | 5e+03      |
|    mean_reward          | 2.1e+03    |
| time/                   |            |
|    total_timesteps      | 985344     |
| train/                  |            |
|    approx_kl            | 0.02131417 |
|    clip_fraction        | 0.227      |
|    clip_range           | 0.2        |
|    entropy_loss         | -15.6      |
|    explained_variance   | 0.981      |
|    learning_rate        | 0.0003     |
|    loss                 | 0.259      |
|    n_updates            | 600        |
|    policy_gradient_loss | -0.0243    |
|    std                  | 0.892      |
|    value_loss           | 0.928      |
----------------------------------------
New best mean reward!
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 5e+03    |
|    

In [ ]:
# Cмотрим как отработал
model = PPO.load("train_models/go1")


# vec_env = model.get_env()
obs, info = robot_env.reset()

while True:
    action, _states = model.predict(obs)
    obs, rewards, terminated, truncated, info = robot_env.step(action)
    print("reward:", rewards)
    #vec_env.render("human")

reward: 9.927001095840134e-05
reward: 0.00014522566464865162
reward: 0.00019036109932668344
reward: 0.0002749377337432976
reward: 0.00017763597370403753
reward: 0.0002554440740378473
reward: 0.00027072638797919824
reward: 0.00029437116691673985
reward: 0.0002892936926004756
reward: 0.0003259178095755613
reward: 0.0003232593450776702
reward: 0.0003358517740414957
reward: 0.0003782253124225343
reward: 0.0004177460432099795
reward: 0.00045508726681185545
reward: 0.0004651745431938706
reward: 0.0005068448262198905
reward: 0.0005220080870230806
reward: 0.0004743709731637423
reward: 0.00048517558966652136
reward: 0.0005270121343874242
reward: 0.0005665038133704989
reward: 0.0005588779233654051
reward: 0.0004910758201881228
reward: 0.0004441009031342681
reward: 0.0004176881171133722
reward: 0.0004335090377052646
reward: 0.0004071176790983698
reward: 0.0004543248135925621
reward: 0.0004070566189501544
reward: 0.00041255367112899913
reward: 0.0004212486686087438
reward: 0.0004301466832260549
re

KeyboardInterrupt: 

In [ ]:
robot_env.observation_space["qpos"].contains(qpos)

NameError: name 'qpos' is not defined

In [ ]:
robot_env

In [ ]:
trunk_body_id = mujoco.mj_name2id(robot_env.model, mujoco.mjtObj.mjOBJ_BODY, "trunk")
trunk_position = robot_env.data.xpos[trunk_body_id]  # [x, y, z] в метрах

print("trunk_body_id", trunk_body_id)
print("trunk_position", trunk_position)

print("data.qpos", robot_env.data.qpos[2])

robot_env.data.xpos

trunk_body_id 1
trunk_position [0.   0.   0.27]
data.qpos 0.2701171794950581


array([[ 0.        ,  0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.27      ],
       [ 0.1881    , -0.04675   ,  0.27      ],
       [ 0.1881    , -0.12675   ,  0.27      ],
       [ 0.02125137, -0.12675   ,  0.13759708],
       [ 0.1881    ,  0.04675   ,  0.27      ],
       [ 0.1881    ,  0.12675   ,  0.27      ],
       [ 0.02125137,  0.12675   ,  0.13759708],
       [-0.1881    , -0.04675   ,  0.27      ],
       [-0.1881    , -0.12675   ,  0.27      ],
       [-0.35494863, -0.12675   ,  0.13759708],
       [-0.1881    ,  0.04675   ,  0.27      ],
       [-0.1881    ,  0.12675   ,  0.27      ],
       [-0.35494863,  0.12675   ,  0.13759708]])

In [ ]:
from stable_baselines3.common.vec_env import ShmemVecEnv

ImportError: cannot import name 'ShmemVecEnv' from 'stable_baselines3.common.vec_env' (/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/stable_baselines3/common/vec_env/__init__.py)

In [ ]:
import time
from stable_baselines3.common.vec_env import DummyVecEnv, SubprocVecEnv #, ShmemVecEnv

def benchmark_vec_env(vec_env_class, xml_path, n_envs=4):
    env = vec_env_class([lambda: RobotLearning(xml_path=xml_path) for _ in range(n_envs)])
    
    start_time = time.time()
    env.reset()
    for _ in range(5000):
        actions = [env.action_space.sample() for _ in range(n_envs)]
        env.step(actions)
    
    env.close()
    return time.time() - start_time

# Сравнение
dummy_time = benchmark_vec_env(DummyVecEnv, xml_path, 10)
subproc_time = benchmark_vec_env(SubprocVecEnv, xml_path, 10)
# shmem_time = benchmark_vec_env(SubprocVecEnv, xml_path, 4)



print(f"DummyVecEnv: {dummy_time:.2f} сек")
print(f"SubprocVecEnv: {subproc_time:.2f} сек")
# print(f"ShmemVecEnv: {subproc_time:.2f} сек")





/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:305: UserWarning: WARN: Box high's precision lowered by casting to float32, current high.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:305: UserWarning: WARN: Box high's precision lowered by casting to float32, current high.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym

DummyVecEnv: 15.26 сек
SubprocVecEnv: 9.89 сек


In [ ]:
free_joint = np.array([[-np.inf, np.inf], # Для X
                        [-np.inf, np.inf], # Для Y
                        [0, 10], # Для Z (условно поставили, что робот не может уйти под пол и взлетететь на 10м вверх)
                        [-1, 1], # w - действительная часть кватерниона Определяет величину поворота w = cos(θ/2),  где θ - угол поворота
                        [-1, 1], # x - ось вращения по x
                        [-1, 1], # y - ось вращения по y
                        [-1, 1], # z - ось вращения по z
        ])

# В массиве есть ограничения на qpos (углы поворота) и я беру нижнюю и верхнюю границы
# Функция выдает model.jnt_range выдает ограничения на углы в модели, на углу joint 
# Мне всегдла выдаются, нижнее и верхнее ограничение, поэтому беру первое значение и второе.

# ограничения на FR, FL, RR, RL ноги 
# model.jnt_range[1:]  (нулевой выкидываем, тк он равен 0 - это free_joint, для него мы отдельно выше )
hinge_joints = robot_env.model.jnt_range[1:] 

test_qpos = np.concatenate([free_joint, hinge_joints])

In [ ]:
robot_env.model.jnt_range

array([[ 0.   ,  0.   ],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888]])

In [ ]:
len(test_qpos)

19

In [ ]:
len(robot_env.qpos)

19

In [ ]:
%load_ext autoreload
%autoreload 2


# Cмотрим как отработал
from robot_env import RobotGo1Env

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [ ]:
robot_go1 = RobotGo1Env(xml_path)

/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:235: UserWarning: WARN: Box low's precision lowered by casting to float32, current low.dtype=float64
  gym.logger.warn(
/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/gymnasium/spaces/box.py:305: UserWarning: WARN: Box high's precision lowered by casting to float32, current high.dtype=float64
  gym.logger.warn(


In [ ]:
qpos_initial = robot_go1.data.qpos

print("len qpos_initial", len(qpos_initial))
print("qpos_initial", qpos_initial)

len qpos_initial 19
qpos_initial [0.    0.    0.445 1.    0.    0.    0.    0.    0.    0.    0.    0.
 0.    0.    0.    0.    0.    0.    0.   ]


In [ ]:
robot_go1.observation_space['qpos']

Box([  -inf   -inf  0.    -1.    -1.    -1.    -1.    -0.863 -0.686 -2.818
 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818], [   inf    inf 10.     1.     1.     1.     1.     0.863  4.501 -0.888
  0.863  4.501 -0.888  0.863  4.501 -0.888  0.863  4.501 -0.888], (19,), float32)

In [ ]:
!!!!!!

In [ ]:
model = PPO.load("train_models/go1")
model

In [ ]:
type(model.get_env())

NoneType

In [ ]:
import mujoco

In [ ]:
# Конструирование награды: reward

Положительная награда:

1) Движение по оси X (координаты)
2) Движение по лси X (линейная скрость)
3) Миниму две лапы касаются пола (и либо левая передняя и правая задняя или наоборот)
4) Не сильно поворачивается по оси X видимо, те несильно заваливается
5) За выживание в среде
6) Можно держать углы в все в определенном интервале.
7) Hip вообще в ноль всегда выводить, тк бессмысленно отводить плечо.


Отрицательная награда:
1) Движение по оси Y и Z (координаты)
2) Движение по лси Y (линейная скрость) 
3) Если по оси Z начинается снижение - это плохо влияет
4) Сильно разведение в плечах (это как отжиматься широким хватом)
5) Питч угол

---- Дополнительно ----


        self.energy_penalty_weight = 0.01
        self.smoothness_penalty_weight = 0.1


---- Подумать ---
        # Целевая скорость
        self.target_velocity = np.array([0.5, 0.0, 0.0])  # 0.5 м/с вперед

        # Проверяем ограничения скорости
        for i in range(len(data.qvel)):
            if abs(data.qvel[i]) > self.max_joint_velocity:
                # Наказываем за превышение скорости
                reward -= 10.0

        """Награды могут использовать данные энкодеров"""
        
        # Пример: награда за поддержание желаемых углов суставов
        target_angles = np.array([0.1, -0.5, 0.8, ...])  # желаемые углы
        current_angles = self.data.sensordata[0:24:2]    # текущие углы из энкодеров
        
        angle_error = np.sum(np.square(current_angles - target_angles))
        reward = -angle_error  # штраф за отклонение от целевых углов


def _compute_reward(self):
    reward = 0.0
    
    # Награда за контакты ног (для стабильности)
    contacts = self.get_foot_contacts()
    desired_contacts = np.array([1, 1, 1, 1])  # все ноги на земле
    contact_reward = -np.linalg.norm(contacts - desired_contacts)
    reward += contact_reward * 0.1
    
    # Штраф за слишком много контактов (возможно падение)
    if data.ncon > 10:  # слишком много столкновений
        reward -= 0.5
    
    return reward

In [ ]:
key_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_KEY, 'home')
if key_id >= 0:
    # Устанавливаем состояние из ключевого кадра
    mujoco.mj_resetDataKeyframe(model, data, key_id)

TypeError: mj_name2id(): incompatible function arguments. The following argument types are supported:
    1. (m: mujoco._structs.MjModel, type: typing.SupportsInt, name: str) -> int

Invoked with: <stable_baselines3.ppo.ppo.PPO object at 0x1337c79d0>, <mjtObj.mjOBJ_KEY: 24>, 'home'

In [ ]:
mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_KEY, 'home')

TypeError: mj_name2id(): incompatible function arguments. The following argument types are supported:
    1. (m: mujoco._structs.MjModel, type: typing.SupportsInt, name: str) -> int

Invoked with: <stable_baselines3.ppo.ppo.PPO object at 0x1337c79d0>, <mjtObj.mjOBJ_KEY: 24>, 'home'

In [ ]:
mujoco.mjtObj.mjOBJ_KEY

<mjtObj.mjOBJ_KEY: 24>

In [ ]:
robot_env.observation_space.contains(robot_env._get_obs())

False

In [ ]:
test = robot_env._get_obs()
test

{'qpos': array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
        0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
        0.   ]),
 'qvel': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])}

In [ ]:
len(test['qpos']), len(test['qvel'])

(19, 12)

In [ ]:
type(test['qpos'][0])

numpy.float64

In [ ]:
robot_env.observation_space

Dict('qpos': Box([  -inf   -inf  0.    -1.    -1.    -1.    -1.    -0.863 -0.686 -2.818
 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818], [   inf    inf 10.     1.     1.     1.     1.     0.863  4.501 -0.888
  0.863  4.501 -0.888  0.863  4.501 -0.888  0.863  4.501 -0.888], (19,), float32), 'qvel': Box(-inf, inf, (12,), float32))

In [ ]:
len([  -inf   -inf  0.    -1.    -1.    -1.    -1.    -0.863 -0.686 -2.818
 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818 -0.863 -0.686 -2.818])

SyntaxError: invalid syntax. Perhaps you forgot a comma? (2779260939.py, line 1)

In [ ]:
model.nu

12

In [ ]:
len(data.qvel)

18

In [ ]:
len(data.qvel[6:])

12

In [ ]:
robot_env = RobotLearning(xml_path)

check_env(robot_env)

Error: Expected `Env.step` to return a four or five element tuple, actual number of elements returned: 6.

In [ ]:
robot_env.reset()

({'qpos': array([ 0.  ,  0.  ,  0.27,  1.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.9 ,
         -1.8 ,  0.  ,  0.9 , -1.8 ,  0.  ,  0.9 , -1.8 ,  0.  ,  0.9 ,
         -1.8 ]),
  'qvel': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0.])},
 {'qpos': array([ 0.  ,  0.  ,  0.27,  1.  ,  0.  ,  0.  ,  0.  ,  0.  ,  0.9 ,
         -1.8 ,  0.  ,  0.9 , -1.8 ,  0.  ,  0.9 , -1.8 ,  0.  ,  0.9 ,
         -1.8 ]),
  'qvel': array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
         0.]),
  'is_terminate': None,
  'is_trancate': None})

In [ ]:
model.jnt_range

array([[ 0.   ,  0.   ],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888],
       [-0.863,  0.863],
       [-0.686,  4.501],
       [-2.818, -0.888]])

In [ ]:
check_env(RobotLearning(xml_path))

AssertionError: Dict space element is not an instance of Space: key='qpos', space=[0.    0.    0.445 1.    0.    0.    0.    0.    0.    0.    0.    0.
 0.    0.    0.    0.    0.    0.    0.   ]

In [ ]:
import gymnasium as gym
from gymnasium import spaces
import mujoco
import numpy as np
import os

class Go1Env(gym.Env):
    """
    Среда для обучения робота Unitree GO1 с помощью RL
    """
    
    def __init__(self, 
                 xml_path='robot_models/unitree_go1/scene.xml',
                 control_frequency=100,  # Hz
                 episode_duration=10.0,  # seconds
                 use_flat_obs=True):     # использовать плоские наблюдения для SB3
        super().__init__()
        
        # Загрузка модели
        if not os.path.exists(xml_path):
            raise FileNotFoundError(f"XML file not found: {xml_path}")
        
        self.model = mujoco.MjModel.from_xml_path(xml_path)
        self.data = mujoco.MjData(self.model)
        
        # Настройки времени
        self.control_frequency = control_frequency
        self.dt = 1.0 / control_frequency
        self.model.opt.timestep = self.dt
        
        self.episode_duration = episode_duration
        self.max_episode_steps = int(episode_duration * control_frequency)
        
        # ID важных элементов
        self.trunk_body_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_BODY, "trunk")
        self.foot_site_names = ["FR", "FL", "RR", "RL"]
        
        # Трекинг состояния
        self.episode_time = 0.0
        self.step_count = 0
        self.initial_position = None
        self.previous_action = None
        self.previous_velocities = None
        
        # Параметры вознаграждения
        self.velocity_weight = 1.0
        self.survival_weight = 0.1
        self.energy_weight = 0.01
        self.smoothness_weight = 0.1
        self.orientation_weight = 0.2
        
        # Целевая скорость (м/с)
        self.target_velocity = np.array([0.5, 0.0, 0.0])  # 0.5 м/с вперед
        
        # Определение пространств
        self.use_flat_obs = use_flat_obs
        self.observation_space = self._create_observation_space()
        self.action_space = self._create_action_space()
        
        print(f"Go1Env инициализирован:")
        print(f"  Control frequency: {control_frequency} Hz")
        print(f"  Episode duration: {episode_duration} сек")
        print(f"  Max steps: {self.max_episode_steps}")
        print(f"  Observation space: {self.observation_space}")
        print(f"  Action space: {self.action_space}")

    def _create_observation_space(self):
        """Создание пространства наблюдений"""
        if self.use_flat_obs:
            # Плоское наблюдение для Stable Baselines3
            obs_size = (12 + 12 + 3 + 3 + 3 + 4 + 3)  # joint_pos + joint_vel + euler + ang_vel + lin_vel + contacts + command
            return spaces.Box(
                low=-np.inf, 
                high=np.inf, 
                shape=(obs_size,), 
                dtype=np.float32
            )
        else:
            # Словарное наблюдение
            return spaces.Dict({
                # Проприоцептивная информация
                "joint_positions": spaces.Box(
                    low=-np.pi, high=np.pi, shape=(12,), dtype=np.float32
                ),
                "joint_velocities": spaces.Box(
                    low=-10.0, high=10.0, shape=(12,), dtype=np.float32
                ),
                
                # Ориентация и скорость туловища
                "trunk_orientation": spaces.Box(  # углы Эйлера
                    low=-np.pi, high=np.pi, shape=(3,), dtype=np.float32
                ),
                "trunk_angular_velocity": spaces.Box(
                    low=-5.0, high=5.0, shape=(3,), dtype=np.float32
                ),
                "trunk_linear_velocity": spaces.Box(
                    low=-3.0, high=3.0, shape=(3,), dtype=np.float32
                ),
                
                # Контакты с землей
                "foot_contacts": spaces.Box(
                    low=0, high=1, shape=(4,), dtype=np.float32
                ),
                
                # Команда движения
                "command": spaces.Box(
                    low=-1.0, high=1.0, shape=(3,), dtype=np.float32
                )
            })

    def _create_action_space(self):
        """Создание пространства действий"""
        # Нормализованные целевые позиции суставов [-1, 1]
        return spaces.Box(
            low=-1.0, 
            high=1.0, 
            shape=(12,),  # 12 суставов ног
            dtype=np.float32
        )

    def _scale_action(self, action):
        """Масштабирование действия из [-1, 1] в реальные углы"""
        # Диапазоны суставов из XML
        joint_ranges = np.array([
            [-0.863, 0.863],    # FR_hip
            [-0.686, 4.501],    # FR_thigh
            [-2.818, -0.888],   # FR_calf
            [-0.863, 0.863],    # FL_hip
            [-0.686, 4.501],    # FL_thigh
            [-2.818, -0.888],   # FL_calf
            [-0.863, 0.863],    # RR_hip
            [-0.686, 4.501],    # RR_thigh
            [-2.818, -0.888],   # RR_calf
            [-0.863, 0.863],    # RL_hip
            [-0.686, 4.501],    # RL_thigh
            [-2.818, -0.888]    # RL_calf
        ])
        
        scaled_action = np.zeros_like(action)
        for i in range(12):
            mid = (joint_ranges[i, 0] + joint_ranges[i, 1]) / 2
            scale = (joint_ranges[i, 1] - joint_ranges[i, 0]) / 2
            scaled_action[i] = action[i] * scale + mid
        
        return scaled_action

    def _quat_to_euler(self, quat):
        """Конвертация кватерниона в углы Эйлера [roll, pitch, yaw]"""
        w, x, y, z = quat
        
        # roll (x-axis rotation)
        sinr_cosp = 2 * (w * x + y * z)
        cosr_cosp = 1 - 2 * (x * x + y * y)
        roll = np.arctan2(sinr_cosp, cosr_cosp)
        
        # pitch (y-axis rotation)
        sinp = 2 * (w * y - z * x)
        sinp = np.clip(sinp, -1, 1)
        pitch = np.arcsin(sinp)
        
        # yaw (z-axis rotation)
        siny_cosp = 2 * (w * z + x * y)
        cosy_cosp = 1 - 2 * (y * y + z * z)
        yaw = np.arctan2(siny_cosp, cosy_cosp)
        
        return np.array([roll, pitch, yaw])

    def _get_foot_contacts(self):
        """Определение контактов ног с землей"""
        contacts = np.zeros(4)
        contact_threshold = 0.03  # метров
        
        for i, site_name in enumerate(self.foot_site_names):
            site_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_SITE, site_name)
            if site_id != -1:
                height = self.data.site_xpos[site_id][2]
                contacts[i] = 1.0 if height < contact_threshold else 0.0
        
        return contacts

    def _get_obs(self):
        """Получение наблюдения"""
        mujoco.mj_forward(self.model, self.data)
        
        # Проприоцептивная информация (только hinge joints)
        joint_pos = self.data.qpos[7:19].copy()      # 12 суставов
        joint_vel = self.data.qvel[6:18].copy()      # 12 скоростей
        
        # Ориентация и скорость туловища
        trunk_quat = self.data.qpos[3:7].copy()
        trunk_euler = self._quat_to_euler(trunk_quat)
        trunk_ang_vel = self.data.qvel[3:6].copy()   # угловая скорость
        trunk_lin_vel = self.data.qvel[0:3].copy()   # линейная скорость
        
        # Контакты с землей
        foot_contacts = self._get_foot_contacts()
        
        # Команда движения
        command = self.target_velocity.copy()
        
        if self.use_flat_obs:
            # Плоское наблюдение для SB3
            flat_obs = np.concatenate([
                joint_pos,           # 12
                joint_vel,           # 12
                trunk_euler,         # 3
                trunk_ang_vel,       # 3
                trunk_lin_vel,       # 3
                foot_contacts,       # 4
                command              # 3
            ])                       # Итого: 40 элементов
            return flat_obs.astype(np.float32)
        else:
            # Словарное наблюдение
            return {
                "joint_positions": joint_pos.astype(np.float32),
                "joint_velocities": joint_vel.astype(np.float32),
                "trunk_orientation": trunk_euler.astype(np.float32),
                "trunk_angular_velocity": trunk_ang_vel.astype(np.float32),
                "trunk_linear_velocity": trunk_lin_vel.astype(np.float32),
                "foot_contacts": foot_contacts.astype(np.float32),
                "command": command.astype(np.float32)
            }

    def reset(self, seed=None, options=None):
        """Сброс среды"""
        super().reset(seed=seed)
        
        # Сброс симуляции
        mujoco.mj_resetData(self.model, self.data)
        
        # Случайное начальное состояние (опционально)
        if options and options.get('random_start', False):
            self._randomize_start_position()
        
        # Обновление кинематики
        mujoco.mj_forward(self.model, self.data)
        
        # Сброс трекинга
        self.episode_time = 0.0
        self.step_count = 0
        self.initial_position = self.data.qpos[0:3].copy()
        self.previous_action = np.zeros(12, dtype=np.float32)
        self.previous_velocities = self.data.qvel[6:18].copy()
        
        observation = self._get_obs()
        info = {}
        
        return observation, info

    def _randomize_start_position(self):
        """Случайное начальное положение суставов"""
        for i in range(7, 19):  # hinge joints
            joint_id = i - 7
            jnt_range = self.model.jnt_range[joint_id + 1]  # +1 т.к. free joint первый
            
            if np.any(jnt_range != 0):
                noise = self.np_random.uniform(-0.1, 0.1)
                new_angle = np.clip(
                    self.data.qpos[i] + noise,
                    jnt_range[0], jnt_range[1]
                )
                self.data.qpos[i] = new_angle

    def step(self, action):
        """Шаг симуляции"""
        # Сохраняем действие и применяем его
        self.previous_action = action.copy()
        scaled_action = self._scale_action(action)
        self.data.ctrl[:] = scaled_action
        
        # Шаг симуляции
        mujoco.mj_step(self.model, self.data)
        
        # Обновление трекинга
        self.episode_time += self.dt
        self.step_count += 1
        
        # Получение наблюдения
        observation = self._get_obs()
        
        # Вычисление вознаграждения
        reward = self._compute_reward(action)
        
        # Проверка условий окончания
        terminated = self._check_termination()
        truncated = self._check_truncation()
        
        # Сохранение скоростей для следующего шага
        self.previous_velocities = self.data.qvel[6:18].copy()
        
        info = {
            "episode_time": self.episode_time,
            "step_count": self.step_count,
            "trunk_height": self.data.qpos[2],
            "forward_velocity": self.data.qvel[0],
            "displacement": self.data.qpos[0] - self.initial_position[0]
        }
        
        return observation, reward, terminated, truncated, info

    def _compute_reward(self, action):
        """Вычисление вознаграждения"""
        reward = 0.0
        
        # 1. Награда за движение вперед
        forward_velocity = self.data.qvel[0]
        velocity_reward = forward_velocity * self.velocity_weight
        
        # 2. Награда за выживание
        survival_reward = self.survival_weight
        
        # 3. Штраф за потребление энергии
        action_magnitude = np.linalg.norm(action)
        energy_penalty = -action_magnitude * self.energy_weight
        
        # 4. Штраф за резкие движения
        if self.previous_action is not None:
            action_diff = np.linalg.norm(action - self.previous_action)
            smoothness_penalty = -action_diff * self.smoothness_weight
        else:
            smoothness_penalty = 0.0
        
        # 5. Штраф за наклон туловища
        trunk_quat = self.data.qpos[3:7]
        trunk_euler = self._quat_to_euler(trunk_quat)
        orientation_penalty = -np.abs(trunk_euler[0]) - np.abs(trunk_euler[1])  # roll + pitch
        orientation_penalty *= self.orientation_weight
        
        # Суммируем все компоненты
        reward = (velocity_reward + survival_reward + 
                 energy_penalty + smoothness_penalty + orientation_penalty)
        
        return reward

    def _check_termination(self):
        """Проверка естественного окончания эпизода"""
        # Падение (туловище слишком низко)
        trunk_height = self.data.qpos[2]
        if trunk_height < 0.1:
            return True
        
        # Слишком большой наклон
        trunk_quat = self.data.qpos[3:7]
        trunk_euler = self._quat_to_euler(trunk_quat)
        if abs(trunk_euler[0]) > 0.8 or abs(trunk_euler[1]) > 0.8:  # roll или pitch > ~46°
            return True
        
        return False

    def _check_truncation(self):
        """Проверка искусственного прерывания"""
        return self.step_count >= self.max_episode_steps

    def render(self):
        """Визуализация (опционально)"""
        # Можно добавить MuJoCo viewer здесь
        pass

    def close(self):
        """Очистка ресурсов"""
        pass


# Пример использования со Stable Baselines3
if __name__ == "__main__":
    # Создание среды
    env = Go1Env(
        xml_path='robot_models/unitree_go1/scene.xml',
        control_frequency=100,
        episode_duration=10.0,
        use_flat_obs=True  # для Stable Baselines3
    )
    
    # Тестовый прогон
    print("Тестовый прогон среды...")
    obs, _ = env.reset()
    
    for step in range(100000):
        action = env.action_space.sample()  # случайное действие
        obs, reward, terminated, truncated, info = env.step(action)
        
        print(f"Step {step}: reward={reward:.3f}, height={info['trunk_height']:.3f}, "
              f"velocity={info['forward_velocity']:.3f}")
        
        # if terminated or truncated:
        #     print("Эпизод завершен!")
        #     break
    
    env.close()

Go1Env инициализирован:
  Control frequency: 100 Hz
  Episode duration: 10.0 сек
  Max steps: 1000
  Observation space: Box(-inf, inf, (40,), float32)
  Action space: Box(-1.0, 1.0, (12,), float32)
Тестовый прогон среды...
Step 0: reward=0.115, height=0.445, velocity=0.040
Step 1: reward=0.107, height=0.444, velocity=0.031
Step 2: reward=0.142, height=0.442, velocity=0.068
Step 3: reward=0.095, height=0.438, velocity=0.039
Step 4: reward=0.122, height=0.433, velocity=0.081
Step 5: reward=0.104, height=0.428, velocity=0.071
Step 6: reward=0.054, height=0.422, velocity=0.017
Step 7: reward=0.081, height=0.416, velocity=0.050
Step 8: reward=-0.041, height=0.408, velocity=-0.066
Step 9: reward=0.023, height=0.400, velocity=0.000
Step 10: reward=0.031, height=0.390, velocity=0.008
Step 11: reward=0.084, height=0.379, velocity=0.065
Step 12: reward=0.031, height=0.366, velocity=0.016
Step 13: reward=-0.018, height=0.352, velocity=-0.030
Step 14: reward=-0.048, height=0.338, velocity=-0.068
S

In [ ]:
from stable_baselines3 import PPO, SAC
from stable_baselines3.common.env_checker import check_env

# Проверка среды
env = Go1Env(use_flat_obs=True)
check_env(env)

# Создание модели
model = PPO("MlpPolicy", env, verbose=1, 
            learning_rate=3e-4,
            batch_size=64,
            n_steps=2048)

# Обучение
model.learn(total_timesteps=1_000_000)
model.save("go1_ppo")

# Тестирование
obs, _ = env.reset()
for i in range(1000):
    action, _states = model.predict(obs, deterministic=True)
    obs, reward, terminated, truncated, info = env.step(action)
    
    if terminated or truncated:
        obs, _ = env.reset()

ImportError: cannot import name 'broadcast_to' from 'numpy.lib.stride_tricks' (/Users/admin/ML/Robots/mjenv/lib/python3.11/site-packages/numpy/lib/stride_tricks.py)

In [ ]:

import mujoco
import numpy as np

model = mujoco.MjModel.from_xml_path('robot_models/unitree_go1/scene.xml')
data = mujoco.MjData(model)

print("=== СРАВНЕНИЕ ОГРАНИЧЕНИЙ ===")

# Для коленного сустава FR
joint_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_JOINT, "FR_calf_joint")
actuator_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_ACTUATOR, "FR_calf")

if joint_id != -1 and actuator_id != -1:
    jnt_range = model.jnt_range[joint_id]
    ctrl_range = model.actuator_ctrlrange[actuator_id]
    
    print(f"FR_calf_joint:")
    print(f"  jnt_range:    {jnt_range[0]:.3f} to {jnt_range[1]:.3f} rad")
    print(f"  ctrl_range:   {ctrl_range[0]:.3f} to {ctrl_range[1]:.3f} rad")
    
    # Конвертируем в градусы
    jnt_deg = [np.degrees(jnt_range[0]), np.degrees(jnt_range[1])]
    ctrl_deg = [np.degrees(ctrl_range[0]), np.degrees(ctrl_range[1])]
    print(f"  jnt_range:    {jnt_deg[0]:.1f} to {jnt_deg[1]:.1f}°")
    print(f"  ctrl_range:   {ctrl_deg[0]:.1f} to {ctrl_deg[1]:.1f}°")

=== СРАВНЕНИЕ ОГРАНИЧЕНИЙ ===
FR_calf_joint:
  jnt_range:    -2.818 to -0.888 rad
  ctrl_range:   -2.818 to -0.888 rad
  jnt_range:    -161.5 to -50.9°
  ctrl_range:   -161.5 to -50.9°


In [ ]:
model.jnt_range[1:].shape

(12, 2)

In [ ]:
model.actuator_forcerange[:,0]


array([-23.7 , -23.7 , -35.55, -23.7 , -23.7 , -35.55, -23.7 , -23.7 ,
       -35.55, -23.7 , -23.7 , -35.55])

In [ ]:

print("=== Actuator Limits ===")
for i in range(model.nu):
    name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_ACTUATOR, i)
    ctrlrange = model.actuator_ctrlrange[i]
    forcerange = model.actuator_forcerange[i]
    
    print(f"\n{name}:")
    print(f"  ctrlrange: {ctrlrange[0]:.3f} to {ctrlrange[1]:.3f} rad")
    print(f"  forcerange: {forcerange[0]:.1f} to {forcerange[1]:.1f} N·m")

=== Actuator Limits ===

FR_hip:
  ctrlrange: -0.863 to 0.863 rad
  forcerange: -23.7 to 23.7 N·m

FR_thigh:
  ctrlrange: -0.686 to 4.501 rad
  forcerange: -23.7 to 23.7 N·m

FR_calf:
  ctrlrange: -2.818 to -0.888 rad
  forcerange: -35.5 to 35.5 N·m

FL_hip:
  ctrlrange: -0.863 to 0.863 rad
  forcerange: -23.7 to 23.7 N·m

FL_thigh:
  ctrlrange: -0.686 to 4.501 rad
  forcerange: -23.7 to 23.7 N·m

FL_calf:
  ctrlrange: -2.818 to -0.888 rad
  forcerange: -35.5 to 35.5 N·m

RR_hip:
  ctrlrange: -0.863 to 0.863 rad
  forcerange: -23.7 to 23.7 N·m

RR_thigh:
  ctrlrange: -0.686 to 4.501 rad
  forcerange: -23.7 to 23.7 N·m

RR_calf:
  ctrlrange: -2.818 to -0.888 rad
  forcerange: -35.5 to 35.5 N·m

RL_hip:
  ctrlrange: -0.863 to 0.863 rad
  forcerange: -23.7 to 23.7 N·m

RL_thigh:
  ctrlrange: -0.686 to 4.501 rad
  forcerange: -23.7 to 23.7 N·m

RL_calf:
  ctrlrange: -2.818 to -0.888 rad
  forcerange: -35.5 to 35.5 N·m


In [ ]:
robot = RobotLearning(xml_path)

In [ ]:
robot.get_detailed_joint_info()

Detailed Joint Information:
ID:  0 | free_joint      | Type: FREE   | 6DOF (position + orientation)
ID:  1 | FR_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  2 | FR_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  3 | FR_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID:  4 | FL_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  5 | FL_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  6 | FL_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID:  7 | RR_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  8 | RR_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  9 | RR_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID: 10 | RL_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID: 11 | RL_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID: 12 

In [ ]:
model.jnt_actfrcrange

array([[0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.],
       [0., 0.]])

In [ ]:
model.actuator_forcerange

array([[-23.7 ,  23.7 ],
       [-23.7 ,  23.7 ],
       [-35.55,  35.55],
       [-23.7 ,  23.7 ],
       [-23.7 ,  23.7 ],
       [-35.55,  35.55],
       [-23.7 ,  23.7 ],
       [-23.7 ,  23.7 ],
       [-35.55,  35.55],
       [-23.7 ,  23.7 ],
       [-23.7 ,  23.7 ],
       [-35.55,  35.55]])

In [ ]:
model.jnt_limited

array([0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=uint8)

In [ ]:
mujoco.mjtTrn.mjTRN_JOINT

<mjtTrn.mjTRN_JOINT: 0>

In [ ]:
data.qpos


array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   ])

In [ ]:
data.qvel

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0.])

In [ ]:
len(data.qvel)

18

In [ ]:
len(data.qpos)

19

In [ ]:
# data.mj_name2id(1)

mujoco.mj_id2name(model, 3, 2)

'FR_thigh_joint'

In [ ]:
mujoco.mj_id2name(model, 3, 0)

In [ ]:
model.jnt_range[0]

array([0., 0.])

In [ ]:
data.qpos[model.jnt_qposadr[0]]

np.float64(0.0)

In [ ]:
mujoco.mjtObj.mjOBJ_JOINT.value

3

In [ ]:
len(model.jnt_range[1:])

12

In [ ]:
mujoco.mjtObj.

In [ ]:

model.njnt

13

In [ ]:
     d = {'joint_id': 
          'joint_name': 
          'joint_contraince'
     }

In [ ]:
mujoco.mjtJoint.mjJNT_BALL

<mjtJoint.mjJNT_BALL: 1>

In [ ]:
import mujoco
import numpy as np

def get_detailed_joint_info(xml_path):
    """
    Расширенная информация о суставах
    """
    model = mujoco.MjModel.from_xml_path(xml_path)
    
    d = {}
    
    for i in range(model.njnt):
        joint_name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_JOINT, i)
        joint_range = model.jnt_range[i]
        
        # Определяем тип сустава
        joint_type = {
            mujoco.mjtJoint.mjJNT_FREE: "FREE",
            mujoco.mjtJoint.mjJNT_BALL: "BALL", 
            mujoco.mjtJoint.mjJNT_SLIDE: "SLIDE",
            mujoco.mjtJoint.mjJNT_HINGE: "HINGE"
        }.get(model.jnt_type[i], "UNKNOWN")
        
        # Форматируем ограничения
        if model.jnt_type[i] == mujoco.mjtJoint.mjJNT_FREE:
            constraint = "6DOF (position + orientation)"
        elif np.all(joint_range == 0):
            constraint = "UNLIMITED"
        else:
            # Конвертируем в градусы для наглядности
            deg_min = np.degrees(joint_range[0])
            deg_max = np.degrees(joint_range[1])
            constraint = f"{joint_range[0]:.3f} to {joint_range[1]:.3f} rad ({deg_min:.1f}° to {deg_max:.1f}°)"
        
        d[i] = {
            'joint_id': i,
            'joint_name': joint_name if joint_name else "free_joint",
            'joint_constraint': constraint,
            'joint_type': joint_type,
            'range_rad': joint_range.tolist(),
            'range_deg': [np.degrees(joint_range[0]), np.degrees(joint_range[1])] if np.any(joint_range != 0) else None
        }
    
    return d

# Получаем детальную информацию
xml_path = 'robot_models/unitree_go1/scene.xml'
detailed_joints = get_detailed_joint_info(xml_path)

print("Detailed Joint Information:")
print("=" * 80)
for joint_id, info in detailed_joints.items():
    # Безопасный вывод с проверкой на None
    name = info['joint_name'] if info['joint_name'] else "free_joint"
    print(f"ID: {info['joint_id']:2d} | {name:15} | Type: {info['joint_type']:6} | {info['joint_constraint']}")

Detailed Joint Information:
ID:  0 | free_joint      | Type: FREE   | 6DOF (position + orientation)
ID:  1 | FR_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  2 | FR_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  3 | FR_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID:  4 | FL_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  5 | FL_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  6 | FL_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID:  7 | RR_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID:  8 | RR_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID:  9 | RR_calf_joint   | Type: HINGE  | -2.818 to -0.888 rad (-161.5° to -50.9°)
ID: 10 | RL_hip_joint    | Type: HINGE  | -0.863 to 0.863 rad (-49.4° to 49.4°)
ID: 11 | RL_thigh_joint  | Type: HINGE  | -0.686 to 4.501 rad (-39.3° to 257.9°)
ID: 12 

In [ ]:
x = "dscsdcs"

print(f"sdcdsc {x} bgfbfg")

sdcdsc dscsdcs bgfbfg


In [ ]:
mujoco.

AttributeError: module 'mujoco' has no attribute 'mjTRN_JOINT'

In [ ]:
mujoco.mjtJoint(3)

<mjtJoint.mjJNT_HINGE: 3>

In [ ]:
# model.njnt - количество joint(ов)

l = []
JOINT_TYPE = {
     0: 'FREE',
     1: 'BALL',
     2: 'SLIDE',
     3: 'HINGE'
}

for i in range(model.njnt):
     # mujoco.mjtObj.mjOBJ_JOINT.value вернет значение 3, те мы только будем смотреть JOINT
     #https://mujoco.readthedocs.io/en/stable/APIreference/APItypes.html#mjtobj



     d = {'joint_id': i, 
          'joint_name': mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_JOINT.value, i),
          'joint_type': JOINT_TYPE[model.jnt_type[i]],
          'joint_contraince': model.jnt_range[i]
     }

     print(d)
     l.append(d)

     

    

#     print(mujoco.mj_id2name(model, 3, i))
#     print(mujoco.mj_id2name(model, 3, i))
    
l

{'joint_id': 0, 'joint_name': None, 'joint_type': 'FREE', 'joint_contraince': array([0., 0.])}
{'joint_id': 1, 'joint_name': 'FR_hip_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.863,  0.863])}
{'joint_id': 2, 'joint_name': 'FR_thigh_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.686,  4.501])}
{'joint_id': 3, 'joint_name': 'FR_calf_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-2.818, -0.888])}
{'joint_id': 4, 'joint_name': 'FL_hip_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.863,  0.863])}
{'joint_id': 5, 'joint_name': 'FL_thigh_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.686,  4.501])}
{'joint_id': 6, 'joint_name': 'FL_calf_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-2.818, -0.888])}
{'joint_id': 7, 'joint_name': 'RR_hip_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.863,  0.863])}
{'joint_id': 8, 'joint_name': 'RR_thigh_joint', 'joint_type': 'HINGE', 'joint_contraince': array([-0.

[{'joint_id': 0,
  'joint_name': None,
  'joint_type': 'FREE',
  'joint_contraince': array([0., 0.])},
 {'joint_id': 1,
  'joint_name': 'FR_hip_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-0.863,  0.863])},
 {'joint_id': 2,
  'joint_name': 'FR_thigh_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-0.686,  4.501])},
 {'joint_id': 3,
  'joint_name': 'FR_calf_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-2.818, -0.888])},
 {'joint_id': 4,
  'joint_name': 'FL_hip_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-0.863,  0.863])},
 {'joint_id': 5,
  'joint_name': 'FL_thigh_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-0.686,  4.501])},
 {'joint_id': 6,
  'joint_name': 'FL_calf_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-2.818, -0.888])},
 {'joint_id': 7,
  'joint_name': 'RR_hip_joint',
  'joint_type': 'HINGE',
  'joint_contraince': array([-0.863,  0.863])},
 {'joint_id': 8,
  'joint_name': 'RR_

In [ ]:
model.jnt_type

array([0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3], dtype=int32)

In [ ]:
model.jnt_group

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [ ]:
len(l)

1

In [ ]:
data.qpos

array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   ])

In [ ]:
      <default class="abduction">
        <joint axis="1 0 0" damping="1" range="-0.863 0.863"/>
        <position ctrlrange="-0.863 0.863"/>
      </default>
      <default class="hip">
        <joint range="-0.686 4.501"/>
        <position ctrlrange="-0.686 4.501"/>
      </default>
      <default class="knee">
        <joint range="-2.818 -0.888"/>
        <position forcerange="-35.55 35.55" ctrlrange="-2.818 -0.888"/>
      </default>

In [ ]:



class CustomEnv(gym.Env):
    """Custom Environment that follows gym interface."""

    metadata = {"render_modes": ["human"], "render_fps": 30}

    def __init__(self, arg1, arg2, ...):
        super().__init__()
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:
        self.action_space = spaces.Discrete(N_DISCRETE_ACTIONS)
        # Example for using image as input (channel-first; channel-last also works):
        self.observation_space = spaces.Box(low=0, high=255,
                                            shape=(N_CHANNELS, HEIGHT, WIDTH), dtype=np.uint8)

    def step(self, action):
        ...
        return observation, reward, terminated, truncated, info

    def reset(self, seed=None, options=None):
        ...
        return observation, info

    def render(self):
        ...

    def close(self):
        ...

In [ ]:
def demonstrate_xquat():
    model = mujoco.MjModel.from_xml_string('''
    <mujoco>
      <worldbody>
        <body name="base" pos="0 0 0.5" euler="0 0 0.8">
          <freejoint/>
          <geom type="box" size="0.1 0.1 0.05"/>
        </body>
      </worldbody>
    </mujoco>
    ''')
    
    data = mujoco.MjData(model)
    mujoco.mj_forward(model, data)
    
    print("=== xquat ДЕМОНСТРАЦИЯ ===")
    print(f"qpos ориентации: {data.qpos[3:7]}")  # локальная ориентация
    
    # xquat - ГЛОБАЛЬНАЯ ориентация
    xquat = data.xquat[1]  # индекс 1 = тело 'base' (индекс 0 = мир)
    print(f"xquat базы: {xquat}")
    
    # Поворачиваем базовое тело
    data.qpos[3:7] = [0.707, 0, 0, 0.707]  # 90° вокруг Z
    mujoco.mj_forward(model, data)
    
    print(f"\nПосле поворота базы на 90°:")
    print(f"xquat базы: {data.xquat[1]}")

demonstrate_xquat()

=== xquat ДЕМОНСТРАЦИЯ ===
qpos ориентации: [0.99997563 0.         0.         0.00698126]
xquat базы: [0.99997563 0.         0.         0.00698126]

После поворота базы на 90°:
xquat базы: [0.70710678 0.         0.         0.70710678]


In [ ]:
def print_go1_sensors(model, data):
    """Специфично для робота Go1"""
    # model = mujoco.MjModel.from_xml_path('scene.xml')
    # data = mujoco.MjData(model)
    
    print("=== СЕНСОРЫ GO1 ===")
    
    # Часто используемые сенсоры в роботах-собаках
    common_sensors = [
        "accelerometer", "gyro", "velocimeter", 
        "jointpos", "jointvel", "touch"
    ]
    
    for i in range(model.nsensor):
        sensor_name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_SENSOR, i)
        sensor_type = model.sensor_type[i]
        
        # Покажем только интересующие нас сенсоры
        type_names = {
            1: "accelerometer", 3: "gyro", 2: "velocimeter",
            8: "jointpos", 9: "jointvel", 0: "touch"
        }
        
        if sensor_type in type_names:
            sensor_type_name = type_names[sensor_type]
            print(f"{sensor_type_name:15} : {sensor_name}")

print_go1_sensors(model, data)


=== СЕНСОРЫ GO1 ===


In [ ]:
import mujoco

def check_go1_sensors():
    global model
    
    print("=== ПРОВЕРКА СЕНСОРОВ GO1 ===")
    print(f"Всего сенсоров: {model.nsensor}")  # Должно быть 0
    
    if model.nsensor == 0:
        print("✅ В go1.xml действительно НЕТ сенсоров!")
    else:
        print("❌ Есть сенсоры, покажем их:")
        for i in range(model.nsensor):
            sensor_name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_SENSOR, i)
            print(f"  - {sensor_name}")

check_go1_sensors()

=== ПРОВЕРКА СЕНСОРОВ GO1 ===
Всего сенсоров: 0
✅ В go1.xml действительно НЕТ сенсоров!


In [ ]:
import mujoco
import numpy as np

def demonstrate_encoders():
    xml = '''
    <mujoco>
      <worldbody>
        <body name="robot" pos="0 0 0.5">
          <joint name="shoulder" type="hinge" axis="0 0 1"/>
          <geom type="capsule" fromto="0 0 0 0.3 0 0" size="0.02"/>
        </body>
      </worldbody>
      
      <sensor>
        <!-- Энкодеры для сустава -->
        <jointpos name="shoulder_position" joint="shoulder"/>
        <jointvel name="shoulder_velocity" joint="shoulder"/>
      </sensor>
    </mujoco>
    '''
    
    model = mujoco.MjModel.from_xml_string(xml)
    data = mujoco.MjData(model)
    
    print("=== ДЕМОНСТРАЦИЯ ЭНКОДЕРОВ ===")
    
    # Поворачиваем сустав
    data.qpos[0] = 0.8  # угол 0.8 радиан (~45°)
    data.qvel[0] = 1.5  # скорость 1.5 рад/с
    
    mujoco.mj_forward(model, data)
    
    # Читаем данные энкодеров
    shoulder_pos = data.sensordata[0]  # jointpos
    shoulder_vel = data.sensordata[1]  # jointvel
    
    print(f"Угол сустава: {shoulder_pos:.3f} рад ({np.degrees(shoulder_pos):.1f}°)")
    print(f"Скорость сустава: {shoulder_vel:.3f} рад/с")
    
    # Сравним с qpos/qvel
    print(f"\nСравнение с qpos/qvel:")
    print(f"qpos[0]: {data.qpos[0]:.3f} рад")
    print(f"qvel[0]: {data.qvel[0]:.3f} рад/с")
    print("→ Энкодеры дублируют qpos/qvel, но в реальном роботе это отдельные датчики!")
    
demonstrate_encoders()

=== ДЕМОНСТРАЦИЯ ЭНКОДЕРОВ ===
Угол сустава: 0.800 рад (45.8°)
Скорость сустава: 1.500 рад/с

Сравнение с qpos/qvel:
qpos[0]: 0.800 рад
qvel[0]: 1.500 рад/с
→ Энкодеры дублируют qpos/qvel, но в реальном роботе это отдельные датчики!


In [ ]:
class Go1Env(gym.Env):
    def __init__(self, xml_path='scene.xml', render=False):
        super(Go1Env, self).__init__()
        
        # Загрузка модели
        self.model = mujoco.MjModel.from_xml_path(xml_path)
        self.data = mujoco.MjData(self.model)
        
        self.render_mode = render
        if render:
            self.viewer = mujoco.viewer.launch_passive(self.model, self.data)
        else:
            self.viewer = None
        
        # Параметры среды
        self.max_episode_steps = 1000
        self.current_step = 0
        
        # Spaces
        self.action_space = spaces.Box(
            low=-1.0, high=1.0, 
            shape=(self.model.nu,), dtype=np.float32
        )
        
        # Observation space: joint positions, velocities, body orientation, etc.
        obs_dim = self.model.nq + self.model.nv + 13  # + body orientation and linear/angular vel
        self.observation_space = spaces.Box(
            low=-np.inf, high=np.inf, 
            shape=(obs_dim,), dtype=np.float32
        )
        
        # Целевая скорость
        self.target_velocity = 1.0  # m/s
        
    def _get_obs(self):
        """Получение наблюдения"""
        # Позиции и скорости суставов
        qpos = self.data.qpos.copy()
        qvel = self.data.qvel.copy()
        
        # Ориентация тела (кватернион) и угловая скорость
        body_orientation = self.data.xquat[1].copy()  # основное тело
        body_lin_vel = self.data.cvel[1][:3].copy()   # линейная скорость
        body_ang_vel = self.data.cvel[1][3:].copy()   # угловая скорость
        
        obs = np.concatenate([
            qpos,
            qvel, 
            body_orientation,
            body_lin_vel,
            body_ang_vel
        ])
        
        return obs
    
    def reset(self, seed=None):
        """Сброс среды"""
        if seed is not None:
            super().reset(seed=seed)
            
        mujoco.mj_resetData(self.model, self.data)
        
        # Небольшая случайная инициализация для разнообразия
        self.data.qpos[7:] += np.random.uniform(-0.1, 0.1, self.model.nq - 7)
        
        self.current_step = 0
        self.previous_base_pos = self.data.qpos[:3].copy()
        
        return self._get_obs(), {}
    
    def step(self, action):
        """Шг симуляции"""
        # Применяем действие
        self.data.ctrl[:] = action * 0.5  # Масштабируем действие
        
        # Шаг симуляции
        mujoco.mj_step(self.model, self.data)
        
        # Получаем наблюдение
        obs = self._get_obs()
        
        # Вычисляем награду
        reward = self._compute_reward()
        
        # Проверяем завершение эпизода
        terminated = self._is_terminated()
        truncated = self.current_step >= self.max_episode_steps
        
        self.current_step += 1
        
        return obs, reward, terminated, truncated, {}
    
    def _compute_reward(self):
        """Вычисление награды"""
        reward = 0.0
        
        # 1. Награда за движение вперед
        current_base_pos = self.data.qpos[:3].copy()
        forward_velocity = (current_base_pos[0] - self.previous_base_pos[0]) / self.model.opt.timestep
        reward += 10.0 * forward_velocity
        
        # Сохраняем позицию для следующего шага
        self.previous_base_pos = current_base_pos
        
        # 2. Штраф за потребление энергии
        power_penalty = 0.001 * np.sum(np.square(self.data.ctrl))
        reward -= power_penalty
        
        # 3. Штраф за падение (наклон тела)
        body_orientation = self.data.xquat[1]
        # Простой способ проверить наклон - использовать z-компоненту
        tilt_penalty = 0.1 * (1.0 - body_orientation[0])  # кватернион w
        reward -= tilt_penalty
        
        # 4. Награда за стабильность (высота тела)
        base_height = self.data.qpos[2]
        target_height = 0.3
        height_reward = -0.1 * abs(base_height - target_height)
        reward += height_reward
        
        return reward
    
    def _is_terminated(self):
        """Проверка завершения эпизода"""
        # Падение (тело слишком низко или слишком наклонено)
        base_height = self.data.qpos[2]
        body_orientation = self.data.xquat[1]
        
        terminated = (
            base_height < 0.15 or  # Слишком низко
            abs(body_orientation[0]) < 0.7  # Слишком сильный наклон
        )
        
        return terminated
    
    def render(self):
        """Рендеринг"""
        if self.viewer is not None:
            self.viewer.sync()
    
    def close(self):
        """Закрытие среды"""
        if self.viewer is not None:
            self.viewer.close()

ModuleNotFoundError: No module named 'gym'

In [ ]:
 1 / 0.002

500.0

In [ ]:
def test_gravity(timestep):
    xml = f"""
    <mujoco>
      <option timestep="{timestep}" gravity="0 0 -9.81"/>
      <worldbody>
        <body name="ball" pos="0 0 10">
          <freejoint/>
          <geom type="sphere" size="0.1"/>
        </body>
      </worldbody>
    </mujoco>
    """
    
    model = mujoco.MjModel.from_xml_string(xml)
    data = mujoco.MjData(model)
    
    heights = []
    while data.time < 2.0:  # 2 секунды симуляции
        mujoco.mj_step(model, data)
        heights.append(data.qpos[2])  # Z-координата
    
    return heights

# Сравним разные timestep
heights_fast = test_gravity(0.01)    # 100 Hz - грубо
heights_slow = test_gravity(0.001)   # 1000 Hz - точно

In [ ]:
len(heights_fast)

200

In [ ]:
len(heights_slow)

2001

In [ ]:
# Реальное время vs симуляционное время
real_start = time.time()
sim_start = data.time

steps = 0
while data.time - sim_start < 5.0:  # 5 секунд симуляции
    mujoco.mj_step(model, data)
    steps += 1
    
    # Синхронизация с реальным временем
    expected_real_time = (data.time - sim_start)
    actual_real_time = time.time() - real_start
    
    if actual_real_time < expected_real_time:
        time.sleep(expected_real_time - actual_real_time)

real_elapsed = time.time() - real_start
print(f"Симуляция {data.time:.2f} сек заняла {real_elapsed:.2f} сек реального времени")
print(f"Эффективный timestep: {real_elapsed / steps:.4f} сек")

Симуляция 5.00 сек заняла 5.00 сек реального времени
Эффективный timestep: 0.0020 сек


In [ ]:

print(f"Шаг времени: {model.opt.timestep} сек")

real_time_start = time.time()
sim_time_start = data.time

for i in range(1000):
    mujoco.mj_step(model, data)
    
    # data.time увеличивается на timestep после каждого mj_step
    print(f"Шаг {i}: симуляционное время = {data.time:.3f} сек")

real_time_elapsed = time.time() - real_time_start
sim_time_elapsed = data.time - sim_time_start

print(f"Реальное время: {real_time_elapsed:.3f} сек")
print(f"Время симуляции: {sim_time_elapsed:.3f} сек")
print(f"Ускорение: {sim_time_elapsed / real_time_elapsed:.1f}x")

Шаг времени: 0.002 сек
Шаг 0: симуляционное время = 5.004 сек
Шаг 1: симуляционное время = 5.006 сек
Шаг 2: симуляционное время = 5.008 сек
Шаг 3: симуляционное время = 5.010 сек
Шаг 4: симуляционное время = 5.012 сек
Шаг 5: симуляционное время = 5.014 сек
Шаг 6: симуляционное время = 5.016 сек
Шаг 7: симуляционное время = 5.018 сек
Шаг 8: симуляционное время = 5.020 сек
Шаг 9: симуляционное время = 5.022 сек
Шаг 10: симуляционное время = 5.024 сек
Шаг 11: симуляционное время = 5.026 сек
Шаг 12: симуляционное время = 5.028 сек
Шаг 13: симуляционное время = 5.030 сек
Шаг 14: симуляционное время = 5.032 сек
Шаг 15: симуляционное время = 5.034 сек
Шаг 16: симуляционное время = 5.036 сек
Шаг 17: симуляционное время = 5.038 сек
Шаг 18: симуляционное время = 5.040 сек
Шаг 19: симуляционное время = 5.042 сек
Шаг 20: симуляционное время = 5.044 сек
Шаг 21: симуляционное время = 5.046 сек
Шаг 22: симуляционное время = 5.048 сек
Шаг 23: симуляционное время = 5.050 сек
Шаг 24: симуляционное время

In [ ]:
import mujoco
import numpy as np

def analyze_go1_states():
    global model 
    global data
    
    print("=== АНАЛИЗ СОСТОЯНИЯ GO1 ===")
    print(f"Размер qpos: {data.qpos.size}")   # Например: 19
    print(f"Размер qvel: {data.qvel.size}")   # Например: 18
    
    # Покажем структуру qpos
    print("\n--- qpos структура ---")
    idx = 0
    
    # 1. Свободное тело (base)
    base_pos = data.qpos[idx:idx+3]
    idx += 3
    base_quat = data.qpos[idx:idx+4]  # кватернион (w, x, y, z)
    idx += 4
    print(f"Base позиция: {base_pos}")
    print(f"Base ориентация: {base_quat}")
    
    # 2. Суставы ног
    joint_names = []
    for i in range(model.njnt):
        name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_JOINT, i)
        joint_names.append(name)
        
    print(f"Суставы: {joint_names}")
    
    # Покажем значения суставов
    for i, name in enumerate(joint_names):
        if name and "base" not in name:  # пропускаем free joint
            joint_pos = data.qpos[idx]
            print(f"Сустав {name}: {joint_pos:.3f} рад")
            idx += 1
    
    # Аналогично для qvel
    print("\n--- qvel структура ---")
    idx = 0
    base_lin_vel = data.qvel[idx:idx+3]
    idx += 3
    base_ang_vel = data.qvel[idx:idx+3]
    idx += 3
    print(f"Base линейная скорость: {base_lin_vel}")
    print(f"Base угловая скорость: {base_ang_vel}")
    
    for i, name in enumerate(joint_names):
        if name and "base" not in name:
            joint_vel = data.qvel[idx]
            print(f"Сустав {name} скорость: {joint_vel:.3f} рад/с")
            idx += 1

# Запуск анализа
analyze_go1_states()

=== АНАЛИЗ СОСТОЯНИЯ GO1 ===
Размер qpos: 19
Размер qvel: 18

--- qpos структура ---
Base позиция: [0.    0.    0.445]
Base ориентация: [1. 0. 0. 0.]
Суставы: [None, 'FR_hip_joint', 'FR_thigh_joint', 'FR_calf_joint', 'FL_hip_joint', 'FL_thigh_joint', 'FL_calf_joint', 'RR_hip_joint', 'RR_thigh_joint', 'RR_calf_joint', 'RL_hip_joint', 'RL_thigh_joint', 'RL_calf_joint']
Сустав FR_hip_joint: 0.000 рад
Сустав FR_thigh_joint: 0.000 рад
Сустав FR_calf_joint: 0.000 рад
Сустав FL_hip_joint: 0.000 рад
Сустав FL_thigh_joint: 0.000 рад
Сустав FL_calf_joint: 0.000 рад
Сустав RR_hip_joint: 0.000 рад
Сустав RR_thigh_joint: 0.000 рад
Сустав RR_calf_joint: 0.000 рад
Сустав RL_hip_joint: 0.000 рад
Сустав RL_thigh_joint: 0.000 рад
Сустав RL_calf_joint: 0.000 рад

--- qvel структура ---
Base линейная скорость: [0. 0. 0.]
Base угловая скорость: [0. 0. 0.]
Сустав FR_hip_joint скорость: 0.000 рад/с
Сустав FR_thigh_joint скорость: 0.000 рад/с
Сустав FR_calf_joint скорость: 0.000 рад/с
Сустав FL_hip_joint скор

In [ ]:
data.qpos

array([0.   , 0.   , 0.445, 1.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   , 0.   ,
       0.   ])

In [ ]:
xml_path = 'robot_models/unitree_go1/scene.xml'

In [ ]:
# Загрузка модели
model = mujoco.MjModel.from_xml_path(xml_path)
data = mujoco.MjData(model)

In [ ]:
model.opt.timestep

0.002

In [ ]:
SIMEND = 10
TIMESTEP = model.opt.timestep
STEP_NUM = int(SIMEND/TIMESTEP)

In [ ]:
STEP_NUM

5000

In [ ]:
obs_dim = self.model.nq + self.model.nv + 13  

5000.0

# Черонвик

In [ ]:
import mujoco
import numpy as np
import mujoco.viewer

#from lxml import etree

In [ ]:
xml_string = """ 
<mujoco>
  <option gravity ="0 0 -9.8" timestep="0.00005"/>

  <worldbody>
    <light diffuse=".5 .5 .5" pos="0 0 3" dir="0 0 -1"/>
    <geom name="red_box" type="box" size=".2 .2 .2" rgba="1 0 0 1"/>
    <geom name="green_sphere" pos=".2 .2 .2" size=".1" rgba="0 1 0 1"/>
    <geom type="plane" size="1 1 0.1" rgba=".9 0 0 1"/>

    <body name="float_body" pos="0 0 2">
      <joint type="free"/>
      <geom  type="box" size=".1 .2 .3" rgba="0 .9 0 1" mass = "1"/>
    </body>

  </worldbody>
</mujoco>
"""

MJCF_MODEL = """ 
<mujoco>
  <option gravity ="0 0 -9.8" timestep="0.00005"/>

  <worldbody>
    <light diffuse=".5 .5 .5" pos="0 0 3" dir="0 0 -1"/>
    <geom name="red_box" type="box" size=".2 .2 .2" rgba="1 0 0 1"/>
    <geom name="green_sphere" pos=".2 .2 .2" size=".1" rgba="0 1 0 1"/>
    <geom type="plane" size="1 1 0.1" rgba=".9 0 0 1"/>

    <body name="float_body" pos="0 0 2">
      <joint type="free"/>
      <geom  type="box" size=".1 .2 .3" rgba="0 .9 0 1" mass = "1"/>
    </body>

  </worldbody>
</mujoco>
"""

In [ ]:
!mjpython --no-raise-error scripts/ex.py

1758.32s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


unknown option --no-raise-error
usage: /Users/admin/ML/Robots/mjenv/bin/python3.11 [option] ... [-c cmd | -m mod | file | -] [arg] ...
Try `python -h' for more information.
^C


In [ ]:
%%script mjpython --no-raise-error
# Этот код выполнится через интерпретатор mjpython
x = 10
y = 20
print(f"Результат: {x + y}")
# Вы можете импортировать модули, которые установлены только для mjpython

Результат: 30


In [ ]:
%%script mjpython --no-raise-error

import mujoco

xml_string = """ 
<mujoco>
  <option gravity ="0 0 -9.8" timestep="0.00005"/>

  <worldbody>
    <light diffuse=".5 .5 .5" pos="0 0 3" dir="0 0 -1"/>
    <geom name="red_box" type="box" size=".2 .2 .2" rgba="1 0 0 1"/>
    <geom name="green_sphere" pos=".2 .2 .2" size=".1" rgba="0 1 0 1"/>
    <geom type="plane" size="1 1 0.1" rgba=".9 0 0 1"/>

    <body name="float_body" pos="0 0 2">
      <joint type="free"/>
      <geom  type="box" size=".1 .2 .3" rgba="0 .9 0 1" mass = "1"/>
    </body>

  </worldbody>
</mujoco>
"""

model = mujoco.MjModel.from_xml_string(xml_string)
data = mujoco.MjData(model)

with mujoco.viewer.launch_passive(model, data) as viewer:
    while viewer.is_running():
        mujoco.mj_step(model, data)
        viewer.sync()

viewer.close()

In [ ]:
import mujoco
with mujoco.viewer.launch_passive(model, data) as viewer:
    while viewer.is_running():
        mujoco.mj_step(model, data)
        viewer.sync()

RuntimeError: `launch_passive` requires that the Python script be run under `mjpython` on macOS

In [ ]:
import time 

with mujoco.viewer.launch_passive(model, data) as viewer:
    start = time.time()

    while viewer.is_running() and time.time() - start < SIMULATION_TIME:
        mujoco.mj_step(model, data)
        viewer.opt.flags[mujoco.mjtVisFlag.mjVIS_CONTACTPOINT] = True
        viewer.opt.flags[mujoco.mjtVisFlag.mjVIS_JOINT] = True
        viewer.sync()

viewer.close()

In [ ]:
!mjpython -V

1793.16s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


Python 3.11.9
^C


In [ ]:
viewer.close()

NameError: name 'viewer' is not defined

In [ ]:
model

In [ ]:
import mujoco

# Loading a specific model description as an imported module.
from robot_descriptions import panda_mj_description
model = mujoco.MjModel.from_xml_path(panda_mj_description.MJCF_PATH)

# Directly loading an instance of MjModel.
from robot_descriptions.loaders.mujoco import load_robot_description
model = load_robot_description("panda_mj_description")

# Loading a variant of the model, e.g. panda without a gripper.
model = load_robot_description("panda_mj_description", variant="panda_nohand")

Cloning https://github.com/deepmind/mujoco_menagerie.git...


100%|██████████| 1977.0/1977.0 [04:44<00:00,  6.96it/s] 


In [ ]:
model.actuator_user

array([], shape=(7, 0), dtype=float64)

# Новое

In [ ]:

# import gym
# from gym import spaces
import numpy as np
import mujoco
import os

import mujoco
import mujoco.viewer
import time
import math
import numpy as np

In [ ]:
def trot_gait(t):
    """Движение рысью"""
    amplitude = 0.8
    frequency = 3.0
    
    controls = np.zeros(12)
    phase = t * frequency
    
    # Диагональные пары ног двигаются вместе
    # FL и RR - одна пара, FR и RL - другая пара
    
    # FL и RR
    swing_phase_1 = math.sin(phase)
    # FR и RL  
    swing_phase_2 = math.sin(phase + math.pi)
    
    # Передняя левая (FL)
    controls[1] = amplitude * swing_phase_1  # hip
    controls[2] = amplitude * max(0, swing_phase_1)  # knee
    
    # Задняя правая (RR)
    controls[10] = amplitude * swing_phase_1  # hip
    controls[11] = amplitude * max(0, swing_phase_1)  # knee
    
    # Передняя правая (FR)
    controls[4] = amplitude * swing_phase_2  # hip
    controls[5] = amplitude * max(0, swing_phase_2)  # knee
    
    # Задняя левая (RL)
    controls[7] = amplitude * swing_phase_2  # hip
    controls[8] = amplitude * max(0, swing_phase_2)  # knee
    
    return controls

In [ ]:
def stand_position():
    """Поза стояния"""
    controls = np.zeros(12)
    # Немного согнутые ноги для устойчивости
    controls[2] = 0.3   # FL knee
    controls[5] = 0.3   # FR knee  
    controls[8] = 0.3   # RL knee
    controls[11] = 0.3  # RR knee
    return controls


In [ ]:
# Загружаем модель из scene.xml
try:
    model = mujoco.MjModel.from_xml_path('robot_models/unitree_go1/scene.xml')
    data = mujoco.MjData(model)
    print("✅ scene.xml успешно загружен!")
except Exception as e:
    print(f"❌ Ошибка загрузки scene.xml: {e}")
    print("Убедитесь, что файл scene.xml и go1.xml находятся в текущей директории")

✅ scene.xml успешно загружен!


In [ ]:
model.opt.gravity

array([ 0.  ,  0.  , -9.81])

In [ ]:
data

In [ ]:
data.qpos[2]

np.float64(0.445)

In [ ]:
# Способ 2: Поиск по имени
joint_name = "FR_hip_joint"
joint_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_JOINT, joint_name)
print(f"\nJoint '{joint_name}' имеет id={joint_id}")


Joint 'FR_hip_joint' имеет id=1


In [ ]:
model.nu

12

In [ ]:
mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_ACTUATOR, "FR_hip_joint")

-1

In [ ]:
print("Actuators и их ctrl индексы:")
for i in range(model.nu):
    actuator_name = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_ACTUATOR, i)
    joint_name = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_JOINT, model.actuator_trnid[i*2])
    print(f"ctrl[{i}] -> {actuator_name} -> joint {joint_name}")

Actuators и их ctrl индексы:


TypeError: mj_name2id(): incompatible function arguments. The following argument types are supported:
    1. (m: mujoco._structs.MjModel, type: typing.SupportsInt, name: str) -> int

Invoked with: <mujoco._structs.MjModel object at 0x111193c70>, <mjtObj.mjOBJ_ACTUATOR: 19>, 0

In [ ]:
def get_actuator_info(model):
    """Получаем информацию о моторах/актюаторах"""
    actuator_info = []
    for i in range(model.nu):
        name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_ACTUATOR, i)
        joint_id = model.actuator_trnid[i, 0]
        joint_name = mujoco.mj_id2name(model, mujoco.mjtObj.mjOBJ_JOINT, joint_id)
        actuator_info.append({
            'index': i,
            'name': name if name else f"actuator_{i}",
            'joint_name': joint_name if joint_name else f"joint_{joint_id}",
            'joint_id': joint_id
        })
    return actuator_info

In [ ]:
get_actuator_info(model)

[{'index': 0,
  'name': 'FR_hip',
  'joint_name': 'FR_hip_joint',
  'joint_id': np.int32(1)},
 {'index': 1,
  'name': 'FR_thigh',
  'joint_name': 'FR_thigh_joint',
  'joint_id': np.int32(2)},
 {'index': 2,
  'name': 'FR_calf',
  'joint_name': 'FR_calf_joint',
  'joint_id': np.int32(3)},
 {'index': 3,
  'name': 'FL_hip',
  'joint_name': 'FL_hip_joint',
  'joint_id': np.int32(4)},
 {'index': 4,
  'name': 'FL_thigh',
  'joint_name': 'FL_thigh_joint',
  'joint_id': np.int32(5)},
 {'index': 5,
  'name': 'FL_calf',
  'joint_name': 'FL_calf_joint',
  'joint_id': np.int32(6)},
 {'index': 6,
  'name': 'RR_hip',
  'joint_name': 'RR_hip_joint',
  'joint_id': np.int32(7)},
 {'index': 7,
  'name': 'RR_thigh',
  'joint_name': 'RR_thigh_joint',
  'joint_id': np.int32(8)},
 {'index': 8,
  'name': 'RR_calf',
  'joint_name': 'RR_calf_joint',
  'joint_id': np.int32(9)},
 {'index': 9,
  'name': 'RL_hip',
  'joint_name': 'RL_hip_joint',
  'joint_id': np.int32(10)},
 {'index': 10,
  'name': 'RL_thigh',
  'j

In [ ]:
class RobotLearning(gym.Env):
    # metadata is a required attribute
    # render_modes in our environment is either None or 'human'.
    # render_fps is not used in our env, but we are require to declare a non-zero value.
    metadata = {"render_modes": ["human"], 'render_fps': 4}

    def __init__(self, xml_path):
        super().__init__()

        self.model = mujoco.MjModel.from_xml_path(xml_path)
        self.data = mujoco.MjData(model)
        

        # Параметры времени
        self.dt = self.model.opt.timestep
        
        # Установим максимальное время с начсала эпизода в секундах
        # Те эпизод не может длится более 100сек, собака может идти 100сек, далее trancked
        self.max_episode_time = 10.0  # секунд
        
        # Трекинг времени эпизода
        self.episode_time = 0.0
        self.step_count = 0
        


        ##### Второй вариант !!!
        
        # Параметры времени
        self.dt = self.model.opt.timestep  # шаг времени в секундах
        self.max_episode_time = 10.0       # максимальное время эпизода в секундах
        self.max_episode_steps = int(self.max_episode_time / self.dt)  # в шагах
        
        # Трекинг времени
        self.episode_start_time = 0.0
        self.current_episode_time = 0.0
        
        self.step_count = 0
        #####


        self.qpos = None
        self.qvel = None


        free_joint = np.array([[-np.inf, np.inf], # Для X
                                [-np.inf, np.inf], # Для Y
                                [0, 10], # Для Z (условно поставили, что робот не может уйти под пол и взлетететь на 10м вверх)
                                [-1, 1], # w - действительная часть кватерниона Определяет величину поворота w = cos(θ/2),  где θ - угол поворота
                                [-1, 1], # x - ось вращения по x
                                [-1, 1], # y - ось вращения по y
                                [-1, 1], # z - ось вращения по z
                ])

        # В массиве есть ограничения на qpos (углы поворота) и я беру нижнюю и верхнюю границы
        # Функция выдает model.jnt_range выдает ограничения на углы в модели, на углу joint 
        # Мне всегдла выдаются, нижнее и верхнее ограничение, поэтому беру первое значение и второе.

        # ограничения на FR, FL, RR, RL ноги 
        # model.jnt_range[1:]  (нулевой выкидываем, тк он равен 0 - это free_joint, для него мы отдельно выше )
        hinge_joints = model.jnt_range[1:] 
        

        qpos_low = np.concat([free_joint, hinge_joints])[:,0]
        qpos_high = np.concat([free_joint, hinge_joints])[:,1]

        # Define what the agent can observe
        # Dict space gives us structured, human-readable observations
        self.observation_space = gym.spaces.Dict(
            {   

                # array([[ 0.   ,  0.   ],
                #    [-0.863,  0.863],
                #    [-0.686,  4.501],
                #    [-2.818, -0.888],
                #    [-0.863,  0.863],
                # model.actuator_forcerange ограничения поданные на акуатор
                 "qpos": gym.spaces.Box(low = qpos_low, high = qpos_high,  shape=(model.nq,), dtype=np.float32),   #  углы с ограничениями
                 "qvel": gym.spaces.Box(low = -np.inf ,high = np.inf, shape=(self.model.nu,), dtype=np.float32),  # [x, y] coordinates
            }
        )


            #    "qpos": gym.spaces.Box(low = model.jnt_range[:,0], high = model.jnt_range[:,1],  shape=(model.jnt_range.shape[0],), dtype=np.float32),   #  углы с ограничениями
            #      "qvel": gym.spaces.Box(low = model.actuator_forcerange[:,0] ,high = model.actuator_forcerange[:,1], shape=(model.actuator_forcerange.shape[0],), dtype=np.float32),  # [x, y] coordinates
  

        # Здесь ставим ограничения актуаторов: нижняя и верхняя границы 
        self.action_space = gym.spaces.Box(low = model.actuator_ctrlrange[:,0] ,high = model.actuator_ctrlrange[:,1], shape=(self.model.nu,), dtype=np.float32)

    def _get_obs(self):
        """Convert internal state to observation format.

        Returns:
            dict: Observation with agent and target positions
        """

        qpos = self.data.qpos.copy()
        qvel = self.data.qvel.copy()
        
        observation_space = {
                "qpos": qpos,  # координаты 
                "qvel": qvel,  # скорости
            }
        
        
        return observation_space
    
    def _get_info(self):
        """Compute auxiliary information for debugging.

        Returns:
            dict: Info with distance between agent and target
        """
        qpose = self.data.qpos.copy()
        qvel = self.data.qvel.copy()
        is_terminate= None
        is_trancate = None
        
        info = {
                "qpos": qpose, # координаты 
                "qvel": qvel,  # скорости
                'is_terminate':is_terminate,
                'is_trancate': is_trancate,

            }
        
        return info
    
    def reset(self, seed=None, options=None):

         # IMPORTANT: Must call this first to seed the random number generator
        super().reset(seed=seed)
        
        mujoco.mj_resetData(self.model, self.data)

        self.episode_start_time = 0
        self.step_count = 0
        
        #  Рандомная инициализация углов ног.
        # !!!! Улучшить эту часть с помощью рандома
        # Вовзращает в состоанияе keyframe, те
        # <keyframe>
        #     <key name="home" qpos="0 0 0.27 1 0 0 0 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8"
        #     ctrl="0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8 0 0.9 -1.8"/>
        # </keyframe>
        key_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_KEY, 'home')
        if key_id >= 0:
            # Устанавливаем состояние из ключевого кадра
            mujoco.mj_resetDataKeyframe(self.model, self.data, key_id)

        # Если устаналивать в key позу, то можно это не писать, тк это автоматически сделаемся в
        # mujoco.mj_resetDataKeyframe(self.model, self.data, key_id)
        self.qpos = self.data.qpos.copy()
        self.qvel = self.data.qvel.copy()


        mujoco.mj_forward(self.model, self.data)

        observation = self._get_obs()
        info = self._get_info()
        
        return observation, info
    

    def _is_terminated(self):
        # trunk_body_id = mujoco.mj_name2id(model, mujoco.mjtObj.mjOBJ_BODY, "trunk")
        # trunk_position = data.xpos[trunk_body_id]  # [x, y, z] в метрах

        hight_on_floor = data.qpos[2] # Берем координату Z

        if hight_on_floor < 0.05:
            return True
        return False
        

    def _is_truncated(self):
        if self.current_episode_time >= self.max_episode_steps or \
            self.max_episode_steps >= self.step_count: 
            return True
        return False
    
    def _compute_reward(self, prev_qpos):
        prev_x = prev_qpos[0]
        current_x = self.data.qpos()[0]

        return np.linalg.norm(current_x - prev_x)

        
    def step(self, action):
        self.current_episode_time += self.dt
        self.step_count +=1
        
        # Предыдущие значения qpos сохраняем для расчета награды
        prev_qpos = self.data.qpose().copy()

        self.data.ctrl[:] = action
        mujoco.mj_step(self.model, self.data)

        observation = self._get_obs()
        info = self._get_info()

        reward = self._compute_reward(prev_qpos)
        terminated = self._is_terminated()
        truncated = self._is_truncated()
        done = None

        return observation, reward, terminated, truncated, info, done

    def render(self):
        """- Renders the environments to help visualise what the agent see, examples modes are “human”, “rgb_array”, “ansi” for text."""
        pass

    def close(self):
        pass


    def get_detailed_joint_info(self):
        """
        Расширенная информация о суставах с ограничениями актуаторов
        """
        
        detailed_joints = {}
        
        for i in range(self.model.njnt):
            joint_name = mujoco.mj_id2name(self.model, mujoco.mjtObj.mjOBJ_JOINT, i)
            joint_range = self.model.jnt_range[i]
            
            # Определяем тип сустава
            joint_type = {
                mujoco.mjtJoint.mjJNT_FREE: "FREE",
                mujoco.mjtJoint.mjJNT_BALL: "BALL", 
                mujoco.mjtJoint.mjJNT_SLIDE: "SLIDE",
                mujoco.mjtJoint.mjJNT_HINGE: "HINGE"
            }.get(self.model.jnt_type[i], "UNKNOWN")
            
            # Ищем соответствующий актуатор для этого сустава
            actuator_ctrlrange = "NO_ACTUATOR"
            actuator_forcerange = "NO_ACTUATOR"
            actuator_name = "NO_ACTUATOR"
            
            if joint_name:  # У free joint нет имени и актуатора
                # Ищем актуатор с таким же именем (обычно naming convention: joint_name = actuator_name + "_joint")
                actuator_search_name = joint_name.replace("_joint", "")
                actuator_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_ACTUATOR, actuator_search_name)
                
                if actuator_id == -1:
                    # Пробуем найти по полному совпадению (иногда имена совпадают)
                    actuator_id = mujoco.mj_name2id(self.model, mujoco.mjtObj.mjOBJ_ACTUATOR, joint_name)
                
                if actuator_id != -1:
                    actuator_name = mujoco.mj_id2name(self.model, mujoco.mjtObj.mjOBJ_ACTUATOR, actuator_id)
                    ctrlrange = self.model.actuator_ctrlrange[actuator_id]
                    forcerange = self.model.actuator_forcerange[actuator_id]
                    
                    # Форматируем ограничения актуаторов
                    if np.any(ctrlrange != 0):
                        ctrl_deg = [np.degrees(ctrlrange[0]), np.degrees(ctrlrange[1])]
                        actuator_ctrlrange = f"{ctrlrange[0]:.3f} to {ctrlrange[1]:.3f} rad ({ctrl_deg[0]:.1f}° to {ctrl_deg[1]:.1f}°)"
                    else:
                        actuator_ctrlrange = "UNLIMITED"
                    
                    if np.any(forcerange != 0):
                        actuator_forcerange = f"{forcerange[0]:.1f} to {forcerange[1]:.1f} N·m"
                    else:
                        actuator_forcerange = "UNLIMITED"
            
            # Форматируем ограничения сустава
            if self.model.jnt_type[i] == mujoco.mjtJoint.mjJNT_FREE:
                constraint = "6DOF (position + orientation)"
            elif np.all(joint_range == 0):
                constraint = "UNLIMITED"
            else:
                # Конвертируем в градусы для наглядности
                deg_min = np.degrees(joint_range[0])
                deg_max = np.degrees(joint_range[1])
                constraint = f"{joint_range[0]:.3f} to {joint_range[1]:.3f} rad ({deg_min:.1f}° to {deg_max:.1f}°)"
            
            detailed_joints[i] = {
                'joint_id': i,
                'joint_name': joint_name if joint_name else "free_joint",
                'joint_constraint': constraint,
                'joint_type': joint_type,
                'range_rad': joint_range.tolist(),
                'range_deg': [np.degrees(joint_range[0]), np.degrees(joint_range[1])] if np.any(joint_range != 0) else None,
                'actuator_name': actuator_name,
                'actuator_ctrlrange': actuator_ctrlrange,
                'actuator_forcerange': actuator_forcerange
            }
        
        # Вывод информации
        print("Detailed Joint and Actuator Information:")
        print("=" * 120)
        for joint_id, info in detailed_joints.items():
            name = info['joint_name']
            print(f"ID: {info['joint_id']:2d} | {name:18} | Type: {info['joint_type']:6} | Joint: {info['joint_constraint']:40} | Actuator: {info['actuator_name']:12} | Ctrl: {info['actuator_ctrlrange']:40} | Force: {info['actuator_forcerange']}")
        
        return detailed_joints
        


